# Note
This notebook contains stuff that was done at an earlier point in time. Therefore some of the things that were done can also be found in other notebooks. The csv-files read at the beginning do not exist in that exact form anymore.

The main reason you see this notebook uploaded is that you can see the pain of manually categorizing the products in the merged dataframe. 
At some point a automized version gets uploaded.

In [1]:
import pandas as pd

In [2]:
orders = pd.read_csv('orders_clean.csv')
orderlines = pd.read_csv('orderlines_clean.csv')
products = pd.read_csv('products_cleaned.csv')
brands = pd.read_csv('brands_clean.csv')

In [3]:
pd.set_option('display.float_format', lambda x: '%.2f' % x)
pd.set_option('display.max_rows', 1000)

### Cleaning the data from rows, which sku does not appear in the products table

In [4]:
orderlines

id  id_order  product_quantity      sku  unit_price  \
0       1119109    299539                 1  OTT0133       18.99   
1       1119110    299540                 1  LGE0043      399.00   
2       1119111    299541                 1  PAR0071      474.05   
3       1119112    299542                 1  WDT0315       68.39   
4       1119113    299543                 1  JBL0104       23.74   
...         ...       ...               ...      ...         ...   
293413  1650199    527398                 1  JBL0122       42.99   
293414  1650200    527399                 1  PAC0653      141.58   
293415  1650201    527400                 2  APP0698        9.99   
293416  1650202    527388                 1  BEZ0204       19.99   
293417  1650203    527401                 1  APP0927       13.99   

                       date  total_price  
0       2017-01-01 00:07:19        18.99  
1       2017-01-01 00:19:45       399.00  
2       2017-01-01 00:20:57       474.05  
3       2017-01-01 00:51:40        68.39  
4       2017-01-01 01:06:38        23.74  
...                     ...          ...  
293413  2018-03-14 13:57:25        42.99  
293414  2018-03-14 13:57:34       141.58  
293415  2018-03-14 13:57:41        19.98  
293416  2018-03-14 13:58:01        19.99  
293417  2018-03-14 13:58:36        13.99  

[293418 rows x 7 columns]

In the next step we want to exclude orders which contain products that do not appear in the products list.
Since orderlines also has a sku column, we can compare the orderlines and products df.
From the code  *orderlines.loc[~orderlines.sku.isin(products.sku)]* we see that 1407 rows contain sku's that do not belong to a product in the product table. So we should remove those from the orders and the orderlines table

Note that right now orderlines hat 293418 rows

In [5]:
orderlines['check_products'] = ~orderlines.sku.isin(products.sku)
orderlines.loc[orderlines.check_products]

id  id_order  product_quantity      sku  unit_price  \
109     1119316    299638                 1  SYN0127      223.24   
180     1119477    299706                 1  EVU0007       28.49   
186     1119494    299712                 1  APP0608      279.99   
240     1119584    299766                 1  APP0607      279.99   
271     1119637    299799                 1  APP0608      279.99   
...         ...       ...               ...      ...         ...   
262950  1601131    491926                 1  REP0088      479.65   
262951  1601133    491926                 1  REP0088       14.31   
262953  1601136    491926                 1  REP0137       54.22   
272613  1617050    510703                 1  PIE0081       16.52   
276274  1623195    515700                 1  PAC0730      197.99   

                       date  total_price  check_products  
109     2017-01-01 11:56:18       223.24            True  
180     2017-01-01 13:57:16        28.49            True  
186     2017-01-01 14:10:47       279.99            True  
240     2017-01-01 16:09:02       279.99            True  
271     2017-01-01 17:09:18       279.99            True  
...                     ...          ...             ...  
262950  2018-02-05 13:17:51       479.65            True  
262951  2018-02-05 13:20:30        14.31            True  
262953  2018-02-05 13:22:01        54.22            True  
272613  2018-02-16 17:15:43        16.52            True  
276274  2018-02-21 21:10:57       197.99            True  

[1414 rows x 8 columns]

Now we should remove every id_order, that contains a product that is not in the list.
Note that every row with such an id_order should be removed, not only the ones with a non-existing sku.
To do this we can create a new table orderlines_id_remove, which is grouped by the id_order and aggregates the False-counts of check_products. If the count is >0, we remove that id_order.
To make life a little easier, I change the check_products column for this: It says True if the sku is NOT in the product list.
Now we can sum up easier.

In [6]:
orderlines_id_remove = orderlines.copy().groupby('id_order').agg({'check_products':'sum'})
orderlines_id_remove.loc[orderlines_id_remove.check_products > 0]

check_products
id_order                
258985                 1
268659                 1
285098                 1
299638                 1
299706                 1
...                  ...
492329                 1
492571                 1
493528                 1
510703                 1
515700                 1

[1384 rows x 1 columns]

We have found 1384 id_orders that can be removed. We keep only those id_orders, where orderlines_id_remove.check_products == 0.
We also reset the index, so that we don't get a key error in the next step.

In [7]:
orderlines_id_remove = orderlines_id_remove.loc[orderlines_id_remove.check_products == 0].reset_index()
orderlines_id_remove

id_order  check_products
0         241319               0
1         241423               0
2         242832               0
3         243330               0
4         243784               0
...          ...             ...
203124    527397               0
203125    527398               0
203126    527399               0
203127    527400               0
203128    527401               0

[203129 rows x 2 columns]

Now we only keep those rows from orderlines, that have an id_order, that appears in orderlines_id_remove

In [8]:
orderlines = orderlines.loc[orderlines.id_order.isin(orderlines_id_remove.id_order)]
orderlines

id  id_order  product_quantity      sku  unit_price  \
0       1119109    299539                 1  OTT0133       18.99   
1       1119110    299540                 1  LGE0043      399.00   
2       1119111    299541                 1  PAR0071      474.05   
3       1119112    299542                 1  WDT0315       68.39   
4       1119113    299543                 1  JBL0104       23.74   
...         ...       ...               ...      ...         ...   
293413  1650199    527398                 1  JBL0122       42.99   
293414  1650200    527399                 1  PAC0653      141.58   
293415  1650201    527400                 2  APP0698        9.99   
293416  1650202    527388                 1  BEZ0204       19.99   
293417  1650203    527401                 1  APP0927       13.99   

                       date  total_price  check_products  
0       2017-01-01 00:07:19        18.99           False  
1       2017-01-01 00:19:45       399.00           False  
2       2017-01-01 00:20:57       474.05           False  
3       2017-01-01 00:51:40        68.39           False  
4       2017-01-01 01:06:38        23.74           False  
...                     ...          ...             ...  
293413  2018-03-14 13:57:25        42.99           False  
293414  2018-03-14 13:57:34       141.58           False  
293415  2018-03-14 13:57:41        19.98           False  
293416  2018-03-14 13:58:01        19.99           False  
293417  2018-03-14 13:58:36        13.99           False  

[290269 rows x 8 columns]

comparing row-counts, we see that about 3000 rows were removed.

Since id_orders matches orders.order_id, we can also remove these rows from orders

In [9]:
orders

order_id         created_date  total_paid            state
0         241319  2017-01-02 13:35:40       44.99        Cancelled
1         241423  2017-11-06 13:10:02      136.15        Completed
2         242832  2017-12-31 17:40:03       15.76        Completed
3         243330  2017-02-16 10:59:38       84.98        Completed
4         243784  2017-11-24 13:35:19      157.86        Cancelled
...          ...                  ...         ...              ...
204508    527397  2018-03-14 13:56:38       42.99      Place Order
204509    527398  2018-03-14 13:57:25       42.99  Shopping Basket
204510    527399  2018-03-14 13:57:34      141.58  Shopping Basket
204511    527400  2018-03-14 13:57:41       19.98  Shopping Basket
204512    527401  2018-03-14 13:58:36       18.98      Place Order

[204513 rows x 4 columns]

In [10]:
orders = orders.loc[orders.order_id.isin(orderlines.id_order)]
orders

order_id         created_date  total_paid            state
0         241319  2017-01-02 13:35:40       44.99        Cancelled
1         241423  2017-11-06 13:10:02      136.15        Completed
2         242832  2017-12-31 17:40:03       15.76        Completed
3         243330  2017-02-16 10:59:38       84.98        Completed
4         243784  2017-11-24 13:35:19      157.86        Cancelled
...          ...                  ...         ...              ...
204508    527397  2018-03-14 13:56:38       42.99      Place Order
204509    527398  2018-03-14 13:57:25       42.99  Shopping Basket
204510    527399  2018-03-14 13:57:34      141.58  Shopping Basket
204511    527400  2018-03-14 13:57:41       19.98  Shopping Basket
204512    527401  2018-03-14 13:58:36       18.98      Place Order

[203129 rows x 4 columns]

about 1400 rows got removed from the orders df.
We don't need the column 'check_products' anymore, so it can be dropped.

In the next step we want to compare the prices of the table orders, orderlines and products. We already looked at orders and orderlines in the other notebook, so we focus on orderlines and products here.
Idea here is to left merge orderlines with products on sku. Since we got rid of every sku that's not in the products table, no problems should arise.

In [11]:
orders.state.value_counts()

Shopping Basket    107136
Completed           46139
Place Order         28506
Pending             14238
Cancelled            7110
Name: state, dtype: int64

In [12]:
orderlines_products = pd.merge(orderlines, products, how = 'left', on='sku')
orderlines_products

id  id_order  product_quantity      sku  unit_price  \
0       1119109    299539                 1  OTT0133       18.99   
1       1119110    299540                 1  LGE0043      399.00   
2       1119111    299541                 1  PAR0071      474.05   
3       1119112    299542                 1  WDT0315       68.39   
4       1119113    299543                 1  JBL0104       23.74   
...         ...       ...               ...      ...         ...   
290264  1650199    527398                 1  JBL0122       42.99   
290265  1650200    527399                 1  PAC0653      141.58   
290266  1650201    527400                 2  APP0698        9.99   
290267  1650202    527388                 1  BEZ0204       19.99   
290268  1650203    527401                 1  APP0927       13.99   

                       date  total_price  check_products  \
0       2017-01-01 00:07:19        18.99           False   
1       2017-01-01 00:19:45       399.00           False   
2       2017-01-01 00:20:57       474.05           False   
3       2017-01-01 00:51:40        68.39           False   
4       2017-01-01 01:06:38        23.74           False   
...                     ...          ...             ...   
290264  2018-03-14 13:57:25        42.99           False   
290265  2018-03-14 13:57:34       141.58           False   
290266  2018-03-14 13:57:41        19.98           False   
290267  2018-03-14 13:58:01        19.99           False   
290268  2018-03-14 13:58:36        13.99           False   

                                                     name  \
0       Otterbox iPhone Case Symmetry 2.0 SE / 5s / 5 ...   
1              27UD58-B LG Monitor 27 "4K UHD DisplayPort   
2       Parrot Bebop 2 White + Command FLYPAD and FPV ...   
3                   Blue WD 2TB Hard Drive 35 "Mac and PC   
4                           Gray Bluetooth Speaker JBL GO   
...                                                   ...   
290264                JBL T450 BT Bluetooth Headset Black   
290265  Samsung SSD 850 expansion kit EVO 250GB + Data...   
290266  Apple Lightning Cable Connector to USB 1m Whit...   
290267            Be.ez LArobe Case Mix Macbook 12 "Green   
290268  EarPods Apple Headphones with Remote and Mic (...   

                                                     desc  price  promo_price  \
0       resistant cover and thin beveled edges for iPh...  34.99        19.99   
1       Monitor for gamers and multimedia professional... 429.00       399.00   
2       cuadricóptero wireless remote control with 25 ... 699.00       569.00   
3       Internal Hard Drive Western Digital 2TB 3.5-in...  79.00        63.99   
4       Compact Bluetooth Handsfree for iPhone iPad an...  29.90        27.99   
...                                                   ...    ...          ...   
290264  Wireless headphones with folding design with 1...  49.95        42.99   
290265  SSD upgrade kit 2008-2010 250 GB MacBook and M... 215.98       141.58   
290266  Apple Lightning USB Cable 1 meter to charge an...  25.00         9.99   
290267                     Macbook thin sheath 12 inches.  29.99        19.99   
290268  EarPods headphones Apple iPhone iPad and iPod ...  35.00        13.99   

        in_stock      type  dots_promo  no_price  price_promo_difference  
0              0  11865403           1     False                 -164.91  
1              0      1296           2     False                -3561.00  
2              0  11905404           2     False                -4990.99  
3              0  12655397           1     False                 -560.95  
4              1      5398           1     False                    1.91  
...          ...       ...         ...       ...                     ...  
290264         1      5384           1     False                 -379.95  
290265         1      1433           2     False                -1199.87  
290266         1      1230           1     False                  -74.90  
290267         0  1

Since I modified some of the prices earlier, I will drop the price_promo_difference for now. Also type, dots_promo and no_price will not be needed

In [13]:
orderlines_products.drop(['type', 'no_price', 'dots_promo', 'price_promo_difference'], axis=1, inplace=True)

It would be interesting to see, if orders make it further in the shopping process when the products have a discount, but we can investigate this question some other time.

For now let's focus on the orders that are completed, since these are the ones that make the actual money. We need the orders table for that.



### Merging all the tables into one



In [14]:
orders_products = orderlines_products.merge(orders, how='left', left_on='id_order', right_on='order_id')
orders_products

id  id_order  product_quantity      sku  unit_price  \
0       1119109    299539                 1  OTT0133       18.99   
1       1119110    299540                 1  LGE0043      399.00   
2       1119111    299541                 1  PAR0071      474.05   
3       1119112    299542                 1  WDT0315       68.39   
4       1119113    299543                 1  JBL0104       23.74   
...         ...       ...               ...      ...         ...   
290264  1650199    527398                 1  JBL0122       42.99   
290265  1650200    527399                 1  PAC0653      141.58   
290266  1650201    527400                 2  APP0698        9.99   
290267  1650202    527388                 1  BEZ0204       19.99   
290268  1650203    527401                 1  APP0927       13.99   

                       date  total_price  check_products  \
0       2017-01-01 00:07:19        18.99           False   
1       2017-01-01 00:19:45       399.00           False   
2       2017-01-01 00:20:57       474.05           False   
3       2017-01-01 00:51:40        68.39           False   
4       2017-01-01 01:06:38        23.74           False   
...                     ...          ...             ...   
290264  2018-03-14 13:57:25        42.99           False   
290265  2018-03-14 13:57:34       141.58           False   
290266  2018-03-14 13:57:41        19.98           False   
290267  2018-03-14 13:58:01        19.99           False   
290268  2018-03-14 13:58:36        13.99           False   

                                                     name  \
0       Otterbox iPhone Case Symmetry 2.0 SE / 5s / 5 ...   
1              27UD58-B LG Monitor 27 "4K UHD DisplayPort   
2       Parrot Bebop 2 White + Command FLYPAD and FPV ...   
3                   Blue WD 2TB Hard Drive 35 "Mac and PC   
4                           Gray Bluetooth Speaker JBL GO   
...                                                   ...   
290264                JBL T450 BT Bluetooth Headset Black   
290265  Samsung SSD 850 expansion kit EVO 250GB + Data...   
290266  Apple Lightning Cable Connector to USB 1m Whit...   
290267            Be.ez LArobe Case Mix Macbook 12 "Green   
290268  EarPods Apple Headphones with Remote and Mic (...   

                                                     desc  price  promo_price  \
0       resistant cover and thin beveled edges for iPh...  34.99        19.99   
1       Monitor for gamers and multimedia professional... 429.00       399.00   
2       cuadricóptero wireless remote control with 25 ... 699.00       569.00   
3       Internal Hard Drive Western Digital 2TB 3.5-in...  79.00        63.99   
4       Compact Bluetooth Handsfree for iPhone iPad an...  29.90        27.99   
...                                                   ...    ...          ...   
290264  Wireless headphones with folding design with 1...  49.95        42.99   
290265  SSD upgrade kit 2008-2010 250 GB MacBook and M... 215.98       141.58   
290266  Apple Lightning USB Cable 1 meter to charge an...  25.00         9.99   
290267                     Macbook thin sheath 12 inches.  29.99        19.99   
290268  EarPods headphones Apple iPhone iPad and iPod ...  35.00        13.99   

        in_stock  order_id         created_date  total_paid            state  
0              0    299539  2017-01-01 00:07:19       18.99  Shopping Basket  
1              0    299540  2017-01-01 00:19:45      399.00  Shopping Basket  
2              0    299541  2017-01-01 00:20:57      474.05  Shopping Basket  
3              0    299542  2017-01-01 00:51:40       68.39  Shopping Basket  
4              1    299543  2017-01-01 01:06:38       23.74  Shopping Basket  
...          ...       ...                  ...         ...              ...  
290264         1    527398  2018-03-14 13:57:25       42.99  Shopping Basket  
290265         1    527399  2018-03-14 13:57:34      141.58  Shopping Basket  
290266         1    527400  2018-03-14 13:57:41       19.9

since we are already merging stuff, let's get the brands here. Well join on short, after extracting the first three letter from the sku.

In [15]:
orders_products['short'] = orders_products.sku.str[:3]
total_orders = orders_products.merge(brands, how='left', on='short')
total_orders.drop(['short', 'check_products', 'id_order', 'id' ],axis=1, inplace=True)
cols = ['order_id', 'sku', 'product_quantity', 'unit_price', 'total_price', 'total_paid', 'price', 'promo_price', 'name', 'date', 'created_date', 'long', 'state', 'desc', 'in_stock']
total_orders = total_orders[cols]
total_orders.rename({'product_quantity':'qty', 'long':'brand'}, axis=1, inplace=True)
total_orders

order_id      sku  qty  unit_price  total_price  total_paid  price  \
0         299539  OTT0133    1       18.99        18.99       18.99  34.99   
1         299540  LGE0043    1      399.00       399.00      399.00 429.00   
2         299541  PAR0071    1      474.05       474.05      474.05 699.00   
3         299542  WDT0315    1       68.39        68.39       68.39  79.00   
4         299543  JBL0104    1       23.74        23.74       23.74  29.90   
...          ...      ...  ...         ...          ...         ...    ...   
290264    527398  JBL0122    1       42.99        42.99       42.99  49.95   
290265    527399  PAC0653    1      141.58       141.58      141.58 215.98   
290266    527400  APP0698    2        9.99        19.98       19.98  25.00   
290267    527388  BEZ0204    1       19.99        19.99       34.98  29.99   
290268    527401  APP0927    1       13.99        13.99       18.98  35.00   

        promo_price                                               name  \
0             19.99  Otterbox iPhone Case Symmetry 2.0 SE / 5s / 5 ...   
1            399.00         27UD58-B LG Monitor 27 "4K UHD DisplayPort   
2            569.00  Parrot Bebop 2 White + Command FLYPAD and FPV ...   
3             63.99              Blue WD 2TB Hard Drive 35 "Mac and PC   
4             27.99                      Gray Bluetooth Speaker JBL GO   
...             ...                                                ...   
290264        42.99                JBL T450 BT Bluetooth Headset Black   
290265       141.58  Samsung SSD 850 expansion kit EVO 250GB + Data...   
290266         9.99  Apple Lightning Cable Connector to USB 1m Whit...   
290267        19.99            Be.ez LArobe Case Mix Macbook 12 "Green   
290268        13.99  EarPods Apple Headphones with Remote and Mic (...   

                       date         created_date            brand  \
0       2017-01-01 00:07:19  2017-01-01 00:07:19         Otterbox   
1       2017-01-01 00:19:45  2017-01-01 00:19:45               LG   
2       2017-01-01 00:20:57  2017-01-01 00:20:57           Parrot   
3       2017-01-01 00:51:40  2017-01-01 00:51:40  Western Digital   
4       2017-01-01 01:06:38  2017-01-01 01:06:38              JBL   
...                     ...                  ...              ...   
290264  2018-03-14 13:57:25  2018-03-14 13:57:25              JBL   
290265  2018-03-14 13:57:34  2018-03-14 13:57:34             Pack   
290266  2018-03-14 13:57:41  2018-03-14 13:57:41            Apple   
290267  2018-03-14 13:58:01  2018-03-14 13:51:59            Be.ez   
290268  2018-03-14 13:58:36  2018-03-14 13:58:36            Apple   

                  state                                               desc  \
0       Shopping Basket  resistant cover and thin beveled edges for iPh...   
1       Shopping Basket  Monitor for gamers and multimedia professional...   
2       Shopping Basket  cuadricóptero wireless remote control with 25 ...   
3       Shopping Basket  Internal Hard Drive Western Digital 2TB 3.5-in...   
4       Shopping Basket  Compact Bluetooth Handsfree for iPhone iPad an...   
...                 ...                                                ...   
290264  Shopping Basket  Wireless headphones with folding design with 1...   
290265  Shopping Basket  SSD upgrade kit 2008-2010 250 GB MacBook and M...   
290266  Shopping Basket  Apple Lightning USB Cable 1 meter to charge an...   
290267  Shopping Basket                     Macbook thin sheath 12 inches.   
290268      Place Order  EarPods headphones Apple iPhone iPad and iPod ...   

        in_stock  
0              0  
1              0  
2              0  
3              0  
4              1  
...          ...  
290264         1  
290265         1  
290266         1  
290267         0  
290268         1  

[290269 rows x 15 columns]

that's a nice table. now let's limit ourselves to the completed orders. if the dates for these orders do not differ by too much, we can delete one of those too. 

In [16]:
orders_comp = total_orders.loc[total_orders.state == 'Completed'].drop('state', axis =1)
orders_comp['date'] = pd.to_datetime(orders_comp['date'])
orders_comp['created_date'] = pd.to_datetime(orders_comp['created_date'])
orders_comp['date_diff'] = orders_comp['created_date'] -orders_comp['date']
orders_comp.sort_values('date_diff')

order_id        sku  qty  unit_price  total_price  total_paid   price  \
106445    363564    KAN0053    1       78.50        78.50     1109.08   99.99   
106444    363564    APP2136    1     1010.59      1010.59     1109.08 1289.00   
247720    457422    EVU0016    1       16.99        16.99       21.98   29.99   
136891    401847    PAC2143    1     2259.99      2259.99     2259.99 2839.00   
60422     339808    SHE0044    1        6.99         6.99       10.98    9.99   
...          ...        ...  ...         ...          ...         ...     ...   
38347     333665    BEL0198    1       19.99        19.99       66.97   34.99   
59468     352100    LAC0198    1       89.79        89.79       93.78  109.99   
105186    392327  OWC0057-2    1       41.99        41.99      127.97   47.98   
74469     365428    SAM0074    1      150.50       150.50      429.18  179.99   
86146     374535    AKI0025    1       37.99        37.99      218.97   39.00   

        promo_price                                               name  \
106445        94.99  Kanex GoPower external battery 15000mAh USB-C ...   
106444      1252.00            Apple iPad Pro 12.9 "Wi-Fi 512GB Silver   
247720        19.99  Evutec Aergo Ballistic Nylon Case + Support iP...   
136891      2599.00  Apple iMac 27 "Core i5 3.8GHz Retina 5K | 16GB...   
60422          2.99              SwitchEasy iPhone Case 0.35 8/7 White   
...             ...                                                ...   
38347         19.99  Belkin Rockstar Road 4 USB Car Charger 7.2A Black   
59468         90.00  LaCie Porsche Design Mobile Hard Drive Disk US...   
105186        41.99     Mac OWC memory 4GB (2x2GB) SO-DIMM DDR2 800MHz   
74469        134.99                     Samsung 850 EVO SSD Disk 500GB   
86146         37.99     Akitio TT3 adapter Thunderbolt 2 Thunderbolt 3   

                      date        created_date       brand  \
106445 2017-08-28 13:42:45 2017-06-09 19:26:17       Kanex   
106444 2017-08-28 13:42:16 2017-06-09 19:26:17       Apple   
247720 2018-01-26 14:10:23 2017-12-07 23:48:36      Evutec   
136891 2017-10-31 14:40:42 2017-09-19 14:42:11        Pack   
60422  2017-05-05 11:51:14 2017-03-27 19:56:01  SwitchEasy   
...                    ...                 ...         ...   
38347  2017-03-09 16:15:27 2017-07-05 17:47:06      Belkin   
59468  2017-05-03 02:16:00 2017-10-29 11:46:37       LaCie   
105186 2017-08-24 12:11:52 2018-03-06 23:18:06         OWC   
74469  2017-06-14 00:14:30 2017-12-26 01:35:31     Samsung   
86146  2017-07-10 18:02:53 2018-03-06 13:03:52      Akitio   

                                                     desc  in_stock  \
106445  USB 15000mAh Portable Battery and USB-C connec...         0   
106444                 New iPad Pro 12.9 inch Wi-Fi 512GB         0   
247720  Cover with anti-impact nylon plastic and iPhon...         1   
136891  IMac desktop computer 27 inch Retina 5K RAM 16...         1   
60422             Ultra Thin Case for iPhone 8/7 in white         0   
...                                                   ...       ...   
38347   Car Charger with 4 USB ports (1A and 2.4A) for...         1   
59468   Aluminum External Hard Drive 2TB with USB3.0 c...         1   
105186    RAM 4GB (2x2GB) iMac (2008) and MacBook (2009).         0   
74469   SSD hard drive Mac and PC 25 inch 500GB SATA I...         1   
86146   Thunderbolt adapter 3 / USB-C Thunderbolt 2 Ma...         1   

                date_diff  
106445 -80 days +05:43:32  
106444 -80 days +05:44:01  
247720 -50 days +09:38:13  
136891 -42 days +00:01:29  
60422  -39 days +08:04:47  
...                   ...  
38347   118 days 01:31:39  
59468   179 days 09:30:37  
105186  194 days 11:06:14  
74469   195 days 01:21:01  
86146   238 days 19:00:59  

[61322 rows x 15 columns]

After looking into that, there are some outliers, but most of the dates are pretty close and I could see no anomalies in the order...maybe date refers to putting sth in the basket and created_date is created after finishing the order. So I will keep created_date for now

In [17]:
orders_comp.drop(['date', 'date_diff'],axis=1, inplace=True)
orders_comp.rename({'created_date':'order_date'}, axis=1, inplace=True)
orders_comp

order_id        sku  qty  unit_price  total_price  total_paid   price  \
6         299545    OWC0100    1       47.49        47.49       51.48   60.99   
7         299546    IOT0014    1       18.99        18.99       18.99   22.95   
8         295347    APP0700    1       72.19        72.19       72.19   89.00   
10        299549    PAC0929    1     2565.99      2565.99     2565.99 3209.00   
17        299556  CRU0039-A    1       60.90        60.90       65.89   76.99   
...          ...        ...  ...         ...          ...         ...     ...   
289885    525664    TUC0207    1       16.52        16.52       85.73   24.99   
289902    527070    APP0698    2        9.99        19.98       24.97   25.00   
289907    527074    APP0698    2        9.99        19.98       24.97   25.00   
289930    527096    APP0698    3        9.99        29.97       34.96   25.00   
289947    527112    APP0698    1        9.99         9.99       14.98   25.00   

        promo_price                                               name  \
6             49.99  OWC In-line Digital Temperature Sensor Kit HDD...   
7             16.99               iOttie Easy View 2 Car Black Support   
8             64.99  Apple 85W MagSafe 2 charger MacBook Pro screen...   
10          2667.99  Apple iMac 27 "Core i5 3.2GHz Retina 5K | 32GB...   
17            70.70                 (Open) Crucial 240GB SSD 7mm BX200   
...             ...                                                ...   
289885        19.99  Tucano Elements Second Skin Macbook Sleeve 12 ...   
289902         9.99  Apple Lightning Cable Connector to USB 1m Whit...   
289907         9.99  Apple Lightning Cable Connector to USB 1m Whit...   
289930         9.99  Apple Lightning Cable Connector to USB 1m Whit...   
289947         9.99  Apple Lightning Cable Connector to USB 1m Whit...   

                order_date    brand  \
6      2017-01-01 01:51:47      OWC   
7      2017-01-01 01:57:34   iOttie   
8      2017-01-01 02:02:38    Apple   
10     2017-01-02 10:00:20     Pack   
17     2017-01-01 02:30:08  Crucial   
...                    ...      ...   
289885 2018-03-14 11:56:19   Tucano   
289902 2018-03-14 11:50:48    Apple   
289907 2018-03-14 11:51:42    Apple   
289930 2018-03-14 11:58:40    Apple   
289947 2018-03-14 12:03:52    Apple   

                                                     desc  in_stock  
6       Kit temperature sensor for HDD iMac 21 inch an...         1  
7       IPhone car holder 7 plus / 7/6 Plus / 6 / 5s /...         0  
8       Apple MagSafe 2 Charger for MacBook Pro 15-inc...         1  
10      IMac desktop computer 27 inch Retina 5K RAM 32...         0  
17      SSD hard drive and high-speed performance with...         0  
...                                                   ...       ...  
289885  velvety inner protective case for MacBook 12 i...         0  
289902  Apple Lightning USB Cable 1 meter to charge an...         1  
289907  Apple Lightning USB Cable 1 meter to charge an...         1  
289930  Apple Lightning USB Cable 1 meter to charge an...         1  
289947  Apple Lightning USB Cable 1 meter to charge an...         1  

[61322 rows x 13 columns]

# Fixing the products' price issue

Next we'll look at price_differences again. Maybe we find some extreme outliers between the unit price and the price. I know that some (probably many) of the prices had not been fixed by me when I looked at the products table. Let's see how bad it really is.

In [18]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.sort_values('price_diff', ascending = False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid  \
283427    523397    UBI0007    1      359.99       359.99      366.98   
140495    423503    APP2494    1      180.99       180.99      200.98   
207410    470483    APP2494    1      180.99       180.99      200.98   
141562    424462    APP2494    1      208.05       208.05      212.04   
142446    425312    APP2494    1      208.05       208.05      215.04   
143368    329976    APP2494    1      208.05       208.05      541.08   
143600    424537    APP2494    1      219.00       219.00     1967.98   
272841    515481    APP2494    4      219.00       876.00      882.99   
206957    470058    APP2494    1      219.00       219.00      225.99   
248213    499587    APP2494    1      219.00       219.00      493.96   
249100    500071    APP2494    1      219.00       219.00      236.98   
255617    503849    APP2494    1      219.00       219.00      225.99   
265152    509601    APP2494    1      219.00       219.00      223.99   
252892    502051    APP2494    1      219.00       219.00      225.99   
248694    499898    APP2494    1      219.00       219.00      266.97   
120902    406283    APP2494    1      219.00       219.00      225.99   
127746    412417    APP2494    1      219.00       219.00      222.99   
120799    406188    APP2494    1      219.00       219.00      225.99   
127857    412498    APP2494    1      219.00       219.00      677.99   
271534    506891    REP0350    1      199.99       199.99      209.98   
260460    506759    TAD0008    1      159.99       159.99      164.98   
274785    516983    TAD0008    1      177.99       177.99      184.98   
122174    407440  APP2133-A    1     1274.86      1274.86     1274.86   
70688     362010    PAC1670    1     1293.99      1293.99     1293.99   
226208    485605    APP2491    1     1128.34      1128.34     1128.34   
272785    515435    APP2492    1     1329.00      1329.00     1335.99   
220202    482065    APP2492    1     1329.00      1329.00     2547.98   
280196    521166    APP2492    1     1329.00      1329.00     2850.99   
245550    497865    APP2492    1     1329.00      1329.00     1335.99   
220111    480069    APP2492    1     1329.00      1329.00     1329.00   
265099    509552    APP2492    1     1329.00      1329.00     1396.99   
253475    502527    APP2492    1     1329.00      1329.00     1329.00   
220689    482253    APP2491    1     1329.00      1329.00     1329.00   
220743    472802    APP2491    1     1329.00      1329.00     1329.00   
220190    482053    APP2492    1     1329.00      1329.00     1329.00   
221991    482964    APP2492    1     1329.00      1329.00     1329.00   
221422    482555    APP2492    1     1329.00      1329.00     1329.00   
273924    516348    APP2492    1     1329.00      1329.00     1335.99   
229803    485705    APP2491    1     1329.00      1329.00     1329.00   
224439    484433    APP2491    1     1329.00      1329.00     1400.99   
247064    498659    APP2491    1     1329.00      1329.00     1416.98   
277571    519195    APP2492    1     1329.00      1329.00     1427.77   
283271    523269    APP2491    1     1329.00      1329.00     1432.97   
274044    516445    APP2492    1     1329.00      1329.00     1427.77   
231431    488994    APP2492    1     1329.00      1329.00     4243.59   
221435    482570    APP2491    1     1329.00      1329.00     1385.00   
273719    515572    APP2491    1     1329.00      1329.00     1430.97   
223062    483526    APP2492    1     1329.00      1329.00     1329.00   
232100    489168    APP2492    1     1329.00      1329.00     1329.00   
273511    516000    APP2491    1     1329.00      1329.00     1335.99   
222137    483085    APP2492    1     1329.00      1329.00     1382.00   
220043    481911    APP2492    1     1329.00      1329.00     1329.00   
220061    481662    APP2492    1     1329.00      1329.00     1774.99   
288790    526126    APP2492    1     1329.00      1329.00     1335

The tail looks very good. There are people that paid more for the product than they should have to, but the data seems fine. Sometimes I noticed that the total_paid is a multiple of the unit_price, but the qty was 1. Maybe this was a mistake on the buyer's part. 

The head shows anomalies that I expected. Some products have a price 100-times higher than it should (not many though). Some have a price thats 10-times higher. But overall it's clear how to fix this. 
Looks like prices above 15000 have the '100-times'-issue. Let's fix it and look once again.

In [19]:
orders_comp.loc[orders_comp.price > 15000, 'price'] /= 100

In [20]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.sort_values('price', ascending = False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid  \
122174    407440  APP2133-A    1     1274.86      1274.86     1274.86   
70688     362010    PAC1670    1     1293.99      1293.99     1293.99   
221422    482555    APP2492    1     1329.00      1329.00     1329.00   
226775    486051    APP2491    1     1329.00      1329.00     1329.00   
260377    506704    APP2492    1     1329.00      1329.00     1335.99   
273719    515572    APP2491    1     1329.00      1329.00     1430.97   
220743    472802    APP2491    1     1329.00      1329.00     1329.00   
220689    482253    APP2491    1     1329.00      1329.00     1329.00   
220202    482065    APP2492    1     1329.00      1329.00     2547.98   
220190    482053    APP2492    1     1329.00      1329.00     1329.00   
226679    480422    APP2492    1     1329.00      1329.00     1402.99   
220111    480069    APP2492    1     1329.00      1329.00     1329.00   
214726    477079    APP2491    1     1329.00      1329.00     1329.00   
220061    481662    APP2492    1     1329.00      1329.00     1774.99   
252923    502075    APP2491    1     1329.00      1329.00     1383.00   
220043    481911    APP2492    1     1329.00      1329.00     1329.00   
226968    486189    APP2492    1     1329.00      1329.00     1329.00   
219973    481851    APP2491    1     1329.00      1329.00     1329.00   
251166    499794    APP2491    1     1329.00      1329.00     1389.99   
214787    477139    APP2491    1     1329.00      1329.00     1329.00   
236592    492243    APP2491    1     1329.00      1329.00     1329.00   
231431    488994    APP2492    1     1329.00      1329.00     4243.59   
219752    481649    APP2491    1     1329.00      1329.00     1329.00   
219594    481486    APP2491    1     1329.00      1329.00     1329.00   
252358    501759    APP2492    1     1329.00      1329.00     1389.99   
219301    481218    APP2491    1     1329.00      1329.00     1538.96   
237875    493201    APP2491    1     1329.00      1329.00     1485.99   
237898    493217    APP2492    1     1329.00      1329.00     1329.00   
273511    516000    APP2491    1     1329.00      1329.00     1335.99   
277571    519195    APP2492    1     1329.00      1329.00     1427.77   
221435    482570    APP2491    1     1329.00      1329.00     1385.00   
273924    516348    APP2492    1     1329.00      1329.00     1335.99   
221991    482964    APP2492    1     1329.00      1329.00     1329.00   
222137    483085    APP2492    1     1329.00      1329.00     1382.00   
280196    521166    APP2492    1     1329.00      1329.00     2850.99   
225870    485305    APP2492    1     1329.00      1329.00     1329.00   
254400    503107    APP2492    1     1329.00      1329.00     1329.00   
226032    485455    APP2491    1     1329.00      1329.00     1383.00   
265099    509552    APP2492    1     1329.00      1329.00     1396.99   
233588    490393    APP2491    1     1329.00      1329.00     1402.98   
225601    480602    APP2492    1     1329.00      1329.00     1329.00   
274044    516445    APP2492    1     1329.00      1329.00     1427.77   
233674    490453    APP2492    1     1329.00      1329.00     1370.98   
146623    428993    APP2492    1     1329.00      1329.00     1329.00   
224501    484504    APP2492    1     1329.00      1329.00     1329.00   
226071    485483    APP2491    1     1329.00      1329.00     1370.23   
224449    484447    APP2492    1     1329.00      1329.00     1329.00   
224439    484433    APP2491    1     1329.00      1329.00     1400.99   
234211    490861    APP2491    1     1329.00      1329.00     1478.98   
232100    489168    APP2492    1     1329.00      1329.00     1329.00   
214271    476637    APP2491    1     1329.00      1329.00     1329.00   
226178    485231    APP2491    1     1329.00      1329.00     1329.00   
226208    485605    APP2491    1     1128.34      1128.34     1128.34   
235171    491415    APP2491    1     1329.00      1329.00     1329

prices above 8250 have the '10-times'-issue when looking at the orders sorted by price.
After that I'll look at the price difference again.

In [21]:
orders_comp.loc[orders_comp.price > 8250, 'price'] /= 10

In [22]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[orders_comp.brand== 'Repair'].sort_values('price_diff', ascending=False)

order_id      sku  qty  unit_price  total_price  total_paid   price  \
152602    434054  REP0362    1       62.99        62.99       72.98 6999.00   
168514    446237  REP0365    1       62.99        62.99       72.98 6999.00   
116071    402009  REP0348    1       69.99        69.99       79.98 6999.00   
105852    392925  REP0319    1       69.99        69.99       79.98 6999.00   
219762    481658  REP0365    1       69.99        69.99       79.98 6999.00   
54401     347403  REP0391    1       69.99        69.99       79.98 6999.00   
136730    420253  REP0341    1       69.99        69.99       79.98 6999.00   
254639    503297  REP0327    1       69.99        69.99       79.98 6999.00   
267580    511304  REP0369    1       69.99        69.99       79.98 6999.00   
128992    407450  REP0188    1      199.99       199.99      209.98 2099.89   
89316     378330  REP0250    1       59.99        59.99       69.98  699.02   
172630    449529  REP0309    1       53.99        53.99       63.98  599.91   
87259     376469  REP0306    1       59.99        59.99       69.98  599.91   
139852    422962  REP0307    1       59.99        59.99       69.98  599.91   
226153    485561  REP0274    1       59.99        59.99       69.98  599.91   
71439     362722  REP0274    1       59.99        59.99       69.98  599.91   
132160    416287  REP0307    1       59.99        59.99       69.98  599.91   
209678    472490  REP0268    1       39.99        39.99       49.98  399.90   
130940    415245  REP0194    1      129.00       129.00      138.99  179.99   
228385    480784  REP0358    1      249.99       249.99      259.98  299.99   
217446    479506  REP0240    1       39.00        39.00       48.99   69.99   
150630    432503  REP0251    1       35.10        35.10       45.09   59.99   
137570    420980  REP0251    1       39.00        39.00       48.99   59.99   
226053    485476  REP0251    1       39.00        39.00       48.99   59.99   
271211    514156  REP0239    1       39.99        39.99      139.97   59.99   
266818    510869  REP0239    1       39.99        39.99       49.98   59.99   
281652    521962  REP0216    1       39.99        39.99       66.97   49.99   
170776    448084  REP0239    1       53.91        53.91       63.90   59.99   
185126    455593  REP0209    1       98.99        98.99      108.98   99.99   
200087    463850  REP0241    1       59.00        59.00       68.99   59.99   
221846    482830  REP0240    1       69.00        69.00       78.99   69.99   
10975     309777  REP0216    1       49.89        49.89       59.88   49.99   
11471     310239  REP0216    1       49.89        49.89       59.88   49.99   
210767    473396  REP0239    1       59.90        59.90       69.89   59.99   
140135    423200  REP0239    1       59.90        59.90      119.79   59.99   
6661      305885  REP0239    1       59.90        59.90       69.89   59.99   
132012    416173  REP0239    1       59.90        59.90       69.89   59.99   
136077    328172  REP0216    1       49.90        49.90       59.89   49.99   
13206     311721  REP0239    1       59.90        59.90      189.88   59.99   
140134    423200  REP0216    1       49.90        49.90      119.79   49.99   
144050    426689  REP0239    1       59.90        59.90      169.87   59.99   
25245     322258  REP0239    1       59.90        59.90       69.89   59.99   
210969    473589  REP0239    1       59.90        59.90      169.87   59.99   
192500    459133  REP0216    1       49.90        49.90       59.89   49.99   
194853    460627  REP0239    1       59.90        59.90       69.89   59.99   
271534    506891  REP0350    1      199.99       199.99      209.98  199.99   
272540    515253  REP0323    1      109.99       109.99      119.98  109.99   
272799    515445  REP0313    1       99.99        99.99      109.98   99.99   
271210    514156  REP0238    1       89.99        89.99      139.97   89.99   
274903    517022  REP0208    1       59.99        59.99   

The 'Repair' brand is causing problems. I saw it when I first looked into the data. Now is the time to tackle the problem.
Prices above 2000 (or price_diff > 5000) --> divide by 100
price above 300 (or price_diff > 100) --> divide by 10

In [23]:
orders_comp.loc[(orders_comp.brand == 'Repair') & (orders_comp.price_diff > 5000), 'price'] /= 100
orders_comp.loc[(orders_comp.brand == 'Repair') & (orders_comp.price_diff > 100), 'price'] /= 10

In [24]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.sort_values('price_diff', ascending = False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid   price  \
26914     323756    PAC1513    1      644.09       644.09      644.09 8136.69   
15239     313460    PAC1689    1      641.99       641.99      641.99 7756.49   
244575    497033  TRA0044-A    1      494.04       494.04      514.03 7109.00   
79740     370047  SAN0131-A    1       56.93        56.93       61.92 6352.86   
19666     317377    PAC1512    1      571.89       571.89      566.89 6736.69   
74673     365623    APP1709    1      669.00       669.00      669.00 6690.01   
8941      307945    APP0880    1      629.99       629.99      629.99 6628.14   
6321      305574    APP0880    1      629.99       629.99      629.99 6628.14   
25347     322345    APP0880    3      632.99      1898.97     1898.97 6628.14   
8260      307323    APP0879    2      632.99      1265.98     1265.98 6628.11   
320       299860    PAC1516    1      457.89       457.89      457.89 5608.69   
27567     324299    PAC1516    1      460.74       460.74      608.93 5608.69   
13682     312136    PAC1516    1      481.99       481.99      857.96 5608.69   
17312     315218    PAC1516    1      481.99       481.99      481.99 5608.69   
6296      305552    APP1752    1      526.99       526.99      526.99 5528.11   
12959     311514    APP1751    1      527.99       527.99      527.99 5528.11   
6010      305306    APP1751    1      527.99       527.99      527.99 5528.11   
53079     346326    SAN0138    1       44.99        44.99       44.99 5028.03   
68627     360207    SAN0138    1       44.99        44.99       44.99 5028.03   
62157     354461    SAN0138    3       44.99       134.97      134.97 5028.03   
12813     311402    SAN0138    1       49.99        49.99       54.98 5028.03   
28676     325187    SAN0138    1       49.99        49.99       54.98 5028.03   
82590     372464    SAN0138    1       53.99        53.99       58.98 5028.03   
30090     326314    APP0871    1      517.99       517.99      517.99 5428.12   
24853     321907    APP0870    1      517.99       517.99      517.99 5428.12   
31206     327394    APP0871    1      517.99       517.99      517.99 5428.12   
8137      307203    APP0870    1      518.99       518.99      518.99 5428.12   
18958     316687    APP0870    1      518.99       518.99      518.99 5428.12   
21491     318964    APP0869    1      518.99       518.99      558.98 5428.12   
11938     310654    APP0869    1      518.99       518.99      518.99 5428.12   
21526     318990    APP0869    1      518.99       518.99      518.99 5428.12   
14979     313223    APP0869    1      518.99       518.99      518.99 5428.12   
11772     310505    APP0869    1      518.99       518.99      513.99 5428.12   
3853      303234    APP0871    2      539.00      1078.00     1107.98 5428.12   
56287     349123    PAC1481    1      512.99       512.99      512.99 5309.90   
102578    390023    PAC1481    1      520.18       520.18      520.18 5309.90   
106615    393566    PAC1481    1      520.18       520.18      520.18 5309.90   
23622     320470    PAC1647    1      509.99       509.99      622.98 5280.78   
148069    430604    TRA0039    1       42.11        42.11       49.10 4528.06   
159474    439928    TRA0011    1       42.13        42.13       46.12 4528.06   
166973    445143    TRA0011    1       42.13        42.13       54.21 4528.06   
154177    435397    TRA0039    1       42.13        42.13       47.12 4528.06   
3826      303211    TRA0039    1       42.99        42.99       47.98 4528.06   
2699      302095    TRA0039    1       42.99        42.99       72.98 4528.06   
210792    473423    TRA0011    1       43.28        43.28       47.27 4528.06   
67601     359317    TRA0011    1       44.99        44.99       49.98 4528.06   
130951    415257    TRA0039    1       45.28        45.28       52.27 4528.06   
108840    395581    TRA0011    1       45.28        45.28       52.27 4528.06   
275768    517645    TRA0039    1       

I saw some pattern for huge price differences (above 2000):
if unit_price > 100 --> divide by 10
if unit_price < 100 --> divide by 100

In [25]:
orders_comp.loc[(orders_comp.price_diff > 2000) & (orders_comp.unit_price > 100), 'price'] /= 10
orders_comp.loc[(orders_comp.price_diff > 2000) & (orders_comp.unit_price < 100), 'price'] /= 100

In [26]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.sort_values('price_diff', ascending = False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid   price  \
214889    477240    WAC0235    1       18.99        18.99      110.97 1999.04   
212673    475203    WAC0235    1       18.99        18.99       22.98 1999.04   
211243    473855    WAC0235    1       18.99        18.99       23.98 1999.04   
202667    466119    WAC0235    1       19.99        19.99      126.96 1999.04   
64804     356743    WAC0235    1       19.99        19.99       93.97 1999.04   
132155    416282    WAC0235    1       19.99        19.99       24.98 1999.04   
119967    402385    WAC0235    1       19.99        19.99       26.98 1999.04   
254068    502940    WAC0235    1       19.99        19.99       37.96 1999.04   
284035    523894    WDT0400    1      204.99       204.99      211.98 2049.95   
155830    251688    APP2493    1      152.95       152.95      505.76 1990.00   
243986    496940    APP2493    1      157.85       157.85     1646.20 1990.00   
137162    420622    APP2493    1      164.46       164.46      455.73 1990.00   
129608    413727    APP2493    1      164.46       164.46      514.21 1990.00   
120874    398738    APP2493    1      164.46       164.46      184.45 1990.00   
121026    404988    APP2493    2      164.46       328.92      348.92 1990.00   
165512    443553    APP2493    1      185.07       185.07      279.76 1990.00   
171343    448521    APP2493    1      185.07       185.07      190.06 1990.00   
166941    440447    APP2493    1      185.07       185.07     2794.94 1990.00   
165900    444475    APP2493    1      185.07       185.07     3385.87 1990.00   
165127    443953    APP2493    1      185.07       185.07      220.06 1990.00   
157295    438082    APP2493    1      185.07       185.07      281.14 1990.00   
151094    432925    APP2493    1      185.07       185.07      190.06 1990.00   
150874    432703    APP2493    1      185.07       185.07      400.00 1990.00   
160164    440466    APP2493    1      185.07       185.07      322.55 1990.00   
161694    441696    APP2493    1      185.07       185.07      983.87 1990.00   
162540    442349    APP2493    1      185.07       185.07      716.26 1990.00   
167490    445440    APP2493    1      185.07       185.07     2842.05 1990.00   
172864    449746    APP2493    1      185.07       185.07      189.06 1990.00   
157123    437931    APP2493    1      185.07       185.07      189.06 1990.00   
152939    434247    APP2493    1      185.07       185.07      364.85 1990.00   
171182    448387    APP2493    1      185.07       185.07      190.06 1990.00   
228156    486826    APP2493    1      191.00       191.00      191.00 1990.00   
253141    502256    APP2493    1      191.00       191.00      191.00 1990.00   
246264    498337    APP2493    1      191.00       191.00      197.99 1990.00   
254377    499587    APP2493    1      191.00       191.00      493.96 1990.00   
254046    502906    APP2493    1      191.00       191.00      452.99 1990.00   
254440    503144    APP2493    1      191.00       191.00      191.00 1990.00   
229972    488048    APP2493    1      191.00       191.00     1330.00 1990.00   
251886    501428    APP2493    1      191.00       191.00      245.48 1990.00   
237082    492506    APP2493    1      191.00       191.00      386.95 1990.00   
207721    470780    APP2493    1      191.04       191.04      210.63 1990.00   
210809    473439    APP2493    1      191.04       191.04      196.03 1990.00   
214044    476398    APP2493    1      191.04       191.04      238.87 1990.00   
208001    471025    APP2493    1      191.04       191.04      198.03 1990.00   
215628    477917    APP2493    1      191.04       191.04      198.03 1990.00   
208963    471851    APP2493    1      191.04       191.04      577.13 1990.00   
208062    471078    APP2493    1      191.04       191.04      198.03 1990.00   
209743    472542    APP2493    1      191.04       191.04      201.03 1990.00   
217098    479194    APP2493    1      1

made a mistake down the line. but I can fix these at the end, since the diff is now at -7000 for one.
For now I'll do the same as before, but my price_diff will be 1500

In [27]:
orders_comp.loc[(orders_comp.price_diff > 1500) & (orders_comp.unit_price > 100), 'price'] /= 10
orders_comp.loc[(orders_comp.price_diff > 1500) & (orders_comp.unit_price < 100), 'price'] /= 100

In [28]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[(orders_comp.unit_price < 1000) & (~orders_comp.name.str.contains('Second hand')) &(orders_comp.price_diff < 900)].sort_values('price_diff', ascending = False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid   price  \
288441    525824    FIB0007    1       99.99        99.99      136.97  999.94   
283911    523793    FIB0007    1       99.99        99.99      104.98  999.94   
141631    424529  CRU0025-2    1       80.07        80.07      400.37  979.78   
213520    475955  CRU0025-2    1       81.99        81.99      531.06  979.78   
206428    469536  CRU0025-2    1       81.99        81.99       85.98  979.78   
27130     323935  CRU0025-2    1       82.99        82.99       87.98  979.78   
245468    497791  CRU0025-2    1       90.99        90.99       97.98  979.78   
279809    520882  CRU0025-2    1       90.99        90.99       97.98  979.78   
203311    466703  CRU0025-2    1       90.99        90.99       90.99  979.78   
256991    504827  CRU0025-2    1       90.99        90.99       95.98  979.78   
183919    454974  CRU0025-2    1       90.99        90.99      224.56  979.78   
136397    420001  CRU0025-2    1       90.99        90.99       90.99  979.78   
264726    509282  CRU0025-2    1       90.99        90.99       97.98  979.78   
130771    415104  CRU0025-2    1       90.99        90.99      194.56  979.78   
278540    519910  CRU0025-2    1       90.99        90.99       95.98  979.78   
260063    506436  CRU0025-2    1       90.99        90.99      510.14  979.78   
130044    414275  CRU0025-2    1       90.99        90.99      649.15  979.78   
278557    519925  CRU0025-2    1       90.99        90.99       97.98  979.78   
273500    515991  CRU0025-2    1       90.99        90.99       97.98  979.78   
273408    515905  CRU0025-2    1       90.99        90.99      194.97  979.78   
138632    421907  CRU0025-2    1       90.99        90.99       94.98  979.78   
248011    499417  CRU0025-2    1       90.99        90.99       95.98  979.78   
253840    502755  CRU0025-2    1       90.99        90.99       90.99  979.78   
128480    413047  CRU0025-2    1       90.99        90.99       95.98  979.78   
180186    453185  CRU0025-2    1       90.99        90.99       95.98  979.78   
3758      301102  CRU0025-2    1      136.87       136.87      136.87  979.78   
98676     386669    APP2466    1      499.00       499.00      499.00 1269.00   
97573     385702    APP2466    1      499.00       499.00      499.00 1269.00   
97530     385659    APP2465    1      499.00       499.00      499.00 1269.00   
97983     375391    APP2465    1      499.00       499.00      499.00 1269.00   
99919     387722    APP2465    1      499.00       499.00      499.00 1269.00   
97638     385758    APP2466    1      499.00       499.00      499.00 1269.00   
17544     315435  KIN0149-A    2       62.98       125.96      247.94  829.89   
101841    389363    ELG0037    1       65.00        65.00      180.98  799.93   
99026     386978    ELG0037    1       65.00        65.00      110.99  799.93   
98984     386946    ELG0037    1       65.00        65.00      188.99  799.93   
98799     386784    ELG0037    1       65.00        65.00      185.99  799.93   
101015    388675    ELG0037    3       65.00       195.00      390.00  799.93   
153635    430559    WAC0234    1       73.59        73.59      314.41  799.89   
242208    495961    ELG0037    1       79.99        79.99       86.98  799.93   
14863     313125    ELG0037    1       79.99        79.99      175.97  799.93   
15524     313671    ELG0037    1       79.99        79.99      126.98  799.93   
230086    488152    ELG0037    1       79.99        79.99      130.98  799.93   
54554     347535    WAC0234    1       79.99        79.99       79.99  799.89   
69109     360623    WAC0234    1       79.99        79.99       79.99  799.89   
72795     363889    WAC0234    1       79.99        79.99       86.98  799.89   
136658    420196    WAC0234    1       79.99        79.99       79.99  799.89   
131357    415613    WAC0234    1       79.99        79.99       84.98  799.89   
91302     380108    WAC0234    1       

Now we are getting into dangerous territory! There are second hand notebooks and also notebooks with rediculous discounts. We have to be more specific now.

In [29]:
orders_comp.loc[(orders_comp.unit_price < 1000) & (~orders_comp.name.str.contains('Second hand')) &(orders_comp.price_diff > 800), 'price'] /= 10

In [30]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[(orders_comp.unit_price < 100) &(orders_comp.price_diff < 170)].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 37387 entries, 6 to 289947
Data columns (total 14 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     37387 non-null  int64         
 1   sku          37387 non-null  object        
 2   qty          37387 non-null  int64         
 3   unit_price   37387 non-null  float64       
 4   total_price  37387 non-null  float64       
 5   total_paid   37387 non-null  float64       
 6   price        37387 non-null  float64       
 7   promo_price  37387 non-null  float64       
 8   name         37387 non-null  object        
 9   order_date   37387 non-null  datetime64[ns]
 10  brand        37367 non-null  object        
 11  desc         37385 non-null  object        
 12  in_stock     37387 non-null  int64         
 13  price_diff   37387 non-null  float64       
dtypes: datetime64[ns](1), float64(6), int64(3), object(4)
memory usage: 4.3+ MB


In [31]:
orders_comp.loc[(orders_comp.price_diff > 175) & (orders_comp.unit_price < 100),'price'] /= 10

In [32]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[(orders_comp.unit_price < 100) &(orders_comp.price_diff <70)].sort_values('price_diff',ascending=False).head(100)

order_id        sku  qty  unit_price  total_price  total_paid  price  \
269242    512773    MOP0112    1       29.99        29.99       67.94  99.95   
269287    503011    MOP0113    1       29.99        29.99       44.98  99.95   
269635    513152    MOP0110    1       29.99        29.99       34.98  99.95   
269260    512804    MOP0112    1       29.99        29.99       41.97  99.95   
268954    512519    MOP0111    1       29.99        29.99       41.97  99.95   
269328    512861    MOP0113    1       29.99        29.99       42.97  99.95   
269567    513087    MOP0112    1       29.99        29.99       33.98  99.95   
270609    513721    MOP0113    1       29.99        29.99       34.98  99.95   
270666    513773    MOP0113    1       29.99        29.99       36.98  99.95   
269271    512815    MOP0112    1       29.99        29.99       42.97  99.95   
269278    512784    MOP0112    1       29.99        29.99       51.97  99.95   
269503    513036    MOP0113    1       29.99        29.99       78.97  99.95   
269382    512922    MOP0113    1       29.99        29.99       36.98  99.95   
270561    513674    MOP0111    1       29.99        29.99       39.98  99.95   
269434    512976    MOP0113    1       29.99        29.99       61.97  99.95   
269289    512826    MOP0110    1       29.99        29.99       33.98  99.95   
269430    512972    MOP0113    1       29.99        29.99       34.98  99.95   
282941    523020    MOP0111    1       29.99        29.99       34.98  99.95   
268863    512420    MOP0111    1       29.99        29.99       46.97  99.95   
268893    512455    MOP0113    1       29.99        29.99       43.97  99.95   
269393    512929    MOP0112    1       29.99        29.99       33.98  99.95   
268940    512512    MOP0114    1       29.99        29.99       33.98  99.95   
269310    512840    MOP0112    1       29.99        29.99       42.97  99.95   
268905    512471    MOP0111    1       29.99        29.99       33.98  99.95   
272227    512998    MOP0111    1       29.99        29.99       34.98  99.95   
269308    512844    MOP0114    1       29.99        29.99       33.98  99.95   
276157    517972    MOP0113    1       29.99        29.99       33.98  99.95   
269114    512664    MOP0112    1       29.99        29.99       64.97  99.95   
273870    516309    MOP0110    1       29.99        29.99       33.98  99.95   
269944    513326    MOP0110    1       29.99        29.99       52.97  99.95   
271983    514780    MOP0112    1       29.99        29.99       36.98  99.95   
281984    520154    MOP0114    1       29.99        29.99       36.98  99.95   
270975    513958    MOP0113    1       29.99        29.99       34.98  99.95   
269176    512730    MOP0110    1       29.99        29.99       33.98  99.95   
268840    512398    MOP0113    1       29.99        29.99       34.98  99.95   
269122    512664    MOP0114    1       29.99        29.99       64.97  99.95   
269229    512777    MOP0110    1       29.99        29.99       33.98  99.95   
269082    512632    MOP0113    1       29.99        29.99       39.98  99.95   
269357    512895    MOP0113    1       29.99        29.99       34.98  99.95   
268842    512400    MOP0111    1       29.99        29.99       34.98  99.95   
272112    514888    MOP0114    1       29.99        29.99       36.98  99.95   
282352    522554    MOP0113    1       29.99        29.99       36.98  99.95   
271650    514513    MOP0113    1       29.99        29.99       33.98  99.95   
269933    513315    MOP0113    1       29.99        29.99       33.98  99.95   
269705    512668    MOP0113    1       29.99        29.99       34.98  99.95   
269225    512775    MOP0112    1       29.99        29.99       36.98  99.95   
269136    512690    MOP0113    1       29.99        29.99       34.98  99.95   
268856    512416    MOP0114    1       29.99        29.99       34.98  99.95   
269159    512715    MOP0112    1       29.99        29.99       34.98  99.95   
1448    

In [33]:
orders_comp.loc[orders_comp.order_id == 377101, 'price'] /= 10
orders_comp.loc[orders_comp.order_id == 382405, 'price'] /= 10

In [34]:
orders_comp.loc[orders_comp.brand == 'Puro'].sort_values('price_diff', ascending=False)

order_id        sku  qty  unit_price  total_price  total_paid  price  \
68573     360159  PUR0144-A    1        9.18         9.18       23.17 129.91   
19796     317489    PUR0142    1       12.34        12.34       17.33 129.91   
68975     360510    PUR0142    1       12.99        12.99       16.98 129.91   
5959      305257    PUR0142    1       12.99        12.99       16.98 129.91   
62270     354551    PUR0142    1       12.99        12.99       16.98 129.91   
69952     361342    PUR0142    1       12.99        12.99       17.98 129.91   
59384     352024    PUR0142    1       12.99        12.99       27.98 129.91   
54495     347486    PUR0142    1       12.99        12.99       35.96 129.91   
53204     344906    PUR0142    1       12.99        12.99      212.97 129.91   
73707     364746    PUR0142    1       12.99        12.99      421.99 129.91   
28675     325186    PUR0142    1       12.99        12.99       12.99 129.91   
84862     374439    PUR0142    1       12.99        12.99       46.96 129.91   
91223     380035    PUR0142    1       12.99        12.99      475.98 129.91   
130861    412329    PUR0154    1       12.99        12.99       36.97 129.91   
133883    417819    PUR0154    1       12.99        12.99       86.97 129.91   
120746    406150    PUR0154    1       12.99        12.99       56.97 129.91   
53665     346762    PUR0107    1        3.30         3.30      108.27  19.99   
6266      305520    PUR0107    1        3.99         3.99       33.46  19.99   
41670     336548    PUR0122    1        6.99         6.99        6.99  19.99   
164671    428669    PUR0156    1       10.19        10.19       26.92  19.95   
208573    471509    PUR0156    1       10.79        10.79       35.77  19.95   
209639    472452    PUR0156    1       10.79        10.79       28.57  19.95   
140502    423509    PUR0156    1       11.39        11.39       16.38  19.95   
122456    407707    PUR0156    1       11.39        11.39      151.21  19.95   
138716    421966    PUR0156    1       11.99        11.99       96.97  19.95   
273349    515861    PUR0156    1       12.99        12.99       19.98  19.95   
94548     382988    PUR0114    1       13.99        13.99       74.97  19.99   
83991     373708    PUR0128    1       11.50        11.50       70.47  16.99   
262636    508120  PUR0143-A    1       11.65        11.65       33.63  16.95   
226026    485446    PUR0139    1        8.89         8.89      254.88  12.95   
237632    492999    PUR0139    1        8.89         8.89       32.87  12.95   
157113    437903    PUR0160    1       16.14        16.14     1006.28  19.95   
134641    418504    PUR0159    1       16.14        16.14       21.13  19.95   
104978    392149    PUR0139    1        9.99         9.99       13.98  12.95   
115216    401281    PUR0139    1        9.99         9.99      157.93  12.95   
115938    401883    PUR0139    1        9.99         9.99       33.97  12.95   
208014    471039    PUR0152    1        9.99         9.99       13.98  12.95   
153867    435119    PUR0157    2       10.19        20.38       27.37  12.95   
162332    442170    PUR0157    1       10.19        10.19       34.17  12.95   
160274    440543    PUR0157    1       10.19        10.19       17.18  12.95   
168453    446185    PUR0157    1       10.19        10.19       14.18  12.95   
14973     305128    PUR0150    1       10.20        10.20      785.12  12.95   
251890    501432    PUR0155    1       14.44        14.44       18.43  16.95   
209453    472292    PUR0157    1       10.79        10.79       94.56  12.95   
211713    474337    PUR0157    2       10.79        21.58       28.57  12.95   
209638    472452    PUR0157    1       10.79        10.79       28.57  12.95   
142877    425703    PUR0157    1       10.79        10.79       15.78  12.95   
167709    445586    PUR0148    1       11.89        11.89       16.88  13.99   
282813    522925    PUR0149    1       14.99        14.99       91.97  16.95   
123321  

In [35]:
orders_comp.loc[(orders_comp.brand == 'Puro') & (orders_comp.price_diff > 100), 'price'] /= 10

In [36]:
orders_comp.loc[orders_comp.order_id == 387335,'price'] /= 10

In [37]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.sort_values('price_diff').head(100)

order_id      sku  qty  unit_price  total_price  total_paid   price  \
167615    445507  LAC0223    1     8287.80      8287.80     8287.80  979.90   
20767     318345  LAC0217    1     3959.10      3959.10     3959.10 3399.00   
271224    514165  APP2090    1     2610.01      2610.01     2715.99 2305.59   
74907     365831  GTE0106    1     1649.99      1649.99     1649.99 1358.99   
69113     360627  WAC0162    1     2289.99      2289.99     4238.97 2049.90   
6191      305450  GTE0081    3     1549.99      4649.97     5549.95 1358.99   
146039    428397  PAC1388    1      848.32       848.32      962.54  673.70   
7895      306995  LAC0179    1      889.99       889.99      889.99  719.00   
4729      304102  LAC0179    1      889.99       889.99      889.99  719.00   
97876     385961  APP1988    1     1020.33      1020.33     1020.33  889.00   
107625    394467  APP1662    1      660.33       660.33      660.33  529.00   
109910    396512  APP1664    1      660.33       660.33      660.33  529.00   
98236     386273  APP1988    1     1020.33      1020.33     1085.32  889.00   
109728    396371  APP1651    1      880.33       880.33      880.33  749.00   
98167     386208  APP1177    1      770.33       770.33      770.33  639.00   
105359    392487  APP1652    1      880.33       880.33      880.33  749.00   
97787     385899  APP1665    1      660.33       660.33      660.33  529.00   
103263    390630  APP1988    1     1020.33      1020.33     1020.33  889.00   
99510     387389  APP1652    1      880.33       880.33      880.33  749.00   
103589    390915  APP1647    1      770.33       770.33      770.33  639.00   
106008    393063  APP1650    1      880.33       880.33      880.33  749.00   
97708     385835  APP1630    1     1020.33      1020.33     1029.32  889.00   
108413    395191  APP1664    1      660.33       660.33      861.64  529.00   
5143      304505  APP1177    1      769.00       769.00      811.98  639.00   
82956     372785  APP1662    1      659.00       659.00      659.00  529.00   
1186      300686  APP1644    1      769.00       769.00      769.00  639.00   
70479     361402  APP1652    1      879.00       879.00      879.00  749.00   
69042     360564  APP1658    2      769.00      1538.00     2996.00  639.00   
50532     344135  APP1645    1      769.00       769.00      769.00  639.00   
69468     360925  APP1651    1      879.00       879.00      879.00  749.00   
79995     370275  APP1175    1      769.00       769.00     2611.99  639.00   
10694     309530  APP1640    1      909.00       909.00      945.98  779.00   
70256     361634  APP1633    1     1019.00      1019.00     1019.00  889.00   
92431     381172  APP1661    1      769.00       769.00      769.00  639.00   
79778     370092  APP1630    2     1019.00      2038.00     2038.00  889.00   
71113     362390  APP1662    1      659.00       659.00      659.00  529.00   
81501     371532  APP1630    2     1019.00      2038.00     2917.00  889.00   
70925     362223  APP1645    1      769.00       769.00      769.00  639.00   
92432     381173  APP1658    1      769.00       769.00      769.00  639.00   
70619     361961  APP1652    1      879.00       879.00      879.00  749.00   
82639     372504  APP1664    1      659.00       659.00      659.00  529.00   
85116     374666  APP1658    1      769.00       769.00      769.00  639.00   
61171     353622  APP1645    1      769.00       769.00     1152.00  639.00   
7569      306709  APP1646    1      769.00       769.00      769.00  639.00   
7052      306227  APP1644    1      769.00       769.00      769.00  639.00   
60054     351962  APP1642    1      909.00       909.00      964.99  779.00   
63752     355859  APP1633    1     1019.00      1019.00     1078.96  889.00   
96064     384370  APP1652    1      879.00       879.00      939.99  749.00   
59988     352546  APP1644    1      769.00       769.00     1784.99  639.00   
614       300152  APP1647    1      769.00       769.00   

Now fix the mistakes I made along the way

In [38]:
orders_comp.loc[orders_comp.order_id == 445507, 'price'] *= 10

In [39]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[orders_comp.brand == 'Crucial'].sort_values('price_diff').head(10)

order_id        sku  qty  unit_price  total_price  total_paid  price  \
107008    393917  CRU0015-2    2       94.99       189.98      196.97  16.40   
107030    393937  CRU0015-2    1       94.99        94.99      875.16  16.40   
30862     327096  CRU0015-2    1       92.97        92.97       99.96  16.40   
3758      301102  CRU0025-2    1      136.87       136.87      136.87  97.98   
238096    493368  CRU0015-2    1      177.99       177.99      182.98 163.98   
229086    487400  CRU0015-2    2      177.99       355.98      362.97 163.98   
233680    490473  CRU0015-2    1      177.99       177.99      382.97 163.98   
231190    486510    CRU0061    1      149.99       149.99      153.98 139.67   
231418    488989    CRU0061    1      149.99       149.99      153.98 139.67   
237736    493096    CRU0061    1      149.99       149.99      153.98 139.67   

        promo_price                                               name  \
107008      1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
107030      1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
30862       1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
3758          96.99  Crucial memory Mac 8GB (2x4GB) SO-DIMM DDR3 16...   
238096      1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
229086      1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
233680      1629.89  Crucial memory Mac 16GB (2x8GB) SO-DIMM DDR3 1...   
231190       129.99                        Crucial MX500 500GB SSD 7mm   
231418       129.99                        Crucial MX500 500GB SSD 7mm   
237736       129.99                        Crucial MX500 500GB SSD 7mm   

                order_date    brand  \
107008 2017-08-29 15:20:11  Crucial   
107030 2017-08-29 16:16:11  Crucial   
30862  2017-02-21 12:38:51  Crucial   
3758   2017-01-02 22:50:11  Crucial   
238096 2018-01-18 08:25:13  Crucial   
229086 2018-01-10 08:06:48  Crucial   
233680 2018-01-14 12:48:11  Crucial   
231190 2018-01-11 18:19:05  Crucial   
231418 2018-01-11 23:47:42  Crucial   
237736 2018-01-17 17:57:31  Crucial   

                                                     desc  in_stock  \
107008  RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
107030  RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
30862   RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
3758    8GB RAM (2x4GB) SO-DIMM 1600MHZ iMac and Macbo...         1   
238096  RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
229086  RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
233680  RAM 16GB (2x8GB) 135V MacBook Pro iMac (2012/2...         1   
231190  SSD 500GB SATA Hard Disk III (6 Gb / s) for Ma...         1   
231418  SSD 500GB SATA Hard Disk III (6 Gb / s) for Ma...         1   
237736  SSD 500GB SATA Hard Disk III (6 Gb / s) for Ma...         1   

        price_diff  
107008      -78.59  
107030      -78.59  
30862       -76.57  
3758        -38.89  
238096      -14.01  
229086      -14.01  
233680      -14.01  
231190      -10.32  
231418      -10.32  
237736      -10.32

In [40]:
orders_comp.loc[(orders_comp.brand == 'Crucial') &(orders_comp.price_diff < -50), 'price'] *= 10

In [41]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[orders_comp.brand == 'Repair'].sort_values('price_diff').head(100)

order_id      sku  qty  unit_price  total_price  total_paid  price  \
177059    446921  REP0396    1      189.99       189.99      199.98 119.99   
97186     385352  REP0396    1      189.99       189.99      199.98 119.99   
136730    420253  REP0341    1       69.99        69.99       79.98   7.00   
219762    481658  REP0365    1       69.99        69.99       79.98   7.00   
105852    392925  REP0319    1       69.99        69.99       79.98   7.00   
116071    402009  REP0348    1       69.99        69.99       79.98   7.00   
54401     347403  REP0391    1       69.99        69.99       79.98   7.00   
267580    511304  REP0369    1       69.99        69.99       79.98   7.00   
254639    503297  REP0327    1       69.99        69.99       79.98   7.00   
152602    434054  REP0362    1       62.99        62.99       72.98   7.00   
168514    446237  REP0365    1       62.99        62.99       72.98   7.00   
170910    448191  REP0396    1      170.99       170.99      180.98 119.99   
51745     345205  REP0323    1      159.99       159.99      169.98 109.99   
96584     384829  REP0323    1      159.99       159.99      199.97 109.99   
66538     358329  REP0313    1      139.99       139.99      149.98  99.99   
49267     343072  REP0313    1      139.99       139.99      149.98  99.99   
78820     369237  REP0313    1      139.99       139.99      149.98  99.99   
45887     340110  REP0313    1      139.99       139.99      149.98  99.99   
13204     311721  REP0238    1      119.99       119.99      189.88  89.99   
12281     310959  REP0238    1      119.99       119.99      129.98  89.99   
24761     321827  REP0238    1      119.99       119.99      129.98  89.99   
985       300497  REP0134    1       89.99        89.99       99.98  59.99   
112730    399064  REP0301    1       59.99        59.99      189.97  39.99   
180361    453334  REP0300    1      119.99       119.99      129.98  99.99   
112728    399064  REP0300    1      119.99       119.99      189.97  99.99   
113176    399456  REP0300    1      119.99       119.99      129.98  99.99   
233827    490609  REP0270    1       69.90        69.90       79.89  49.99   
121172    406523  REP0151    1       49.99        49.99       59.98  39.99   
104398    391642  REP0238    1       99.99        99.99      109.98  89.99   
103062    390223  REP0151    1       49.99        49.99       59.98  39.99   
98502     386519  REP0238    1       99.99        99.99      109.98  89.99   
200531    464252  REP0238    1       99.99        99.99      109.98  89.99   
79458     369793  REP0238    1       99.99        99.99      109.98  89.99   
203647    466987  REP0238    1       99.99        99.99      109.98  89.99   
210968    473589  REP0238    1       99.99        99.99      169.87  89.99   
135785    419478  REP0238    1       99.99        99.99      109.98  89.99   
83856     373595  REP0238    1       99.99        99.99      109.98  89.99   
81924     371892  REP0238    1       99.99        99.99      109.98  89.99   
76806     367513  REP0238    1       99.99        99.99      138.96  89.99   
144051    426689  REP0238    1       99.99        99.99      169.87  89.99   
53406     346619  REP0238    1       99.99        99.99      169.97  89.99   
248351    499688  REP0238    1       99.99        99.99      129.96  89.99   
58279     351001  REP0151    1       49.99        49.99       59.98  39.99   
58809     351510  REP0238    1       99.99        99.99      109.98  89.99   
60174     352739  REP0238    1       99.99        99.99      109.98  89.99   
66601     358386  REP0151    1       49.99        49.99       59.98  39.99   
53087     346333  REP0238    1       99.99        99.99      109.98  89.99   
91498     380300  REP0208    1       69.99        69.99       79.98  59.99   
60144     352714  REP0207    1       69.99        69.99       79.98  59.99   
67249     358984  REP0207    1       69.99        69.99       79.98  59.99   
208709    471631  REP0134    1

In [42]:
orders_comp.loc[(orders_comp.brand == 'Repair') & (orders_comp.promo_price == 69.99), 'price'] *= 10

In [43]:
orders_comp['price_diff'] = orders_comp['price']-orders_comp['unit_price']
orders_comp.loc[orders_comp.brand == 'Repair'].sort_values('price_diff').head(100)

order_id      sku  qty  unit_price  total_price  total_paid  price  \
97186     385352  REP0396    1      189.99       189.99      199.98 119.99   
177059    446921  REP0396    1      189.99       189.99      199.98 119.99   
170910    448191  REP0396    1      170.99       170.99      180.98 119.99   
96584     384829  REP0323    1      159.99       159.99      199.97 109.99   
51745     345205  REP0323    1      159.99       159.99      169.98 109.99   
66538     358329  REP0313    1      139.99       139.99      149.98  99.99   
78820     369237  REP0313    1      139.99       139.99      149.98  99.99   
49267     343072  REP0313    1      139.99       139.99      149.98  99.99   
45887     340110  REP0313    1      139.99       139.99      149.98  99.99   
12281     310959  REP0238    1      119.99       119.99      129.98  89.99   
13204     311721  REP0238    1      119.99       119.99      189.88  89.99   
24761     321827  REP0238    1      119.99       119.99      129.98  89.99   
985       300497  REP0134    1       89.99        89.99       99.98  59.99   
180361    453334  REP0300    1      119.99       119.99      129.98  99.99   
112728    399064  REP0300    1      119.99       119.99      189.97  99.99   
112730    399064  REP0301    1       59.99        59.99      189.97  39.99   
113176    399456  REP0300    1      119.99       119.99      129.98  99.99   
233827    490609  REP0270    1       69.90        69.90       79.89  49.99   
103062    390223  REP0151    1       49.99        49.99       59.98  39.99   
203647    466987  REP0238    1       99.99        99.99      109.98  89.99   
121172    406523  REP0151    1       49.99        49.99       59.98  39.99   
83856     373595  REP0238    1       99.99        99.99      109.98  89.99   
81924     371892  REP0238    1       99.99        99.99      109.98  89.99   
79458     369793  REP0238    1       99.99        99.99      109.98  89.99   
144051    426689  REP0238    1       99.99        99.99      169.87  89.99   
200531    464252  REP0238    1       99.99        99.99      109.98  89.99   
76806     367513  REP0238    1       99.99        99.99      138.96  89.99   
104398    391642  REP0238    1       99.99        99.99      109.98  89.99   
98502     386519  REP0238    1       99.99        99.99      109.98  89.99   
66601     358386  REP0151    1       49.99        49.99       59.98  39.99   
135785    419478  REP0238    1       99.99        99.99      109.98  89.99   
248351    499688  REP0238    1       99.99        99.99      129.96  89.99   
53087     346333  REP0238    1       99.99        99.99      109.98  89.99   
53406     346619  REP0238    1       99.99        99.99      169.97  89.99   
60174     352739  REP0238    1       99.99        99.99      109.98  89.99   
210968    473589  REP0238    1       99.99        99.99      169.87  89.99   
58809     351510  REP0238    1       99.99        99.99      109.98  89.99   
58279     351001  REP0151    1       49.99        49.99       59.98  39.99   
91498     380300  REP0208    1       69.99        69.99       79.98  59.99   
194213    460184  REP0208    1       69.99        69.99       79.98  59.99   
96531     384773  REP0208    1       69.99        69.99       79.98  59.99   
212558    475093  REP0134    1       69.99        69.99       79.98  59.99   
58186     350906  REP0208    1       69.99        69.99       79.98  59.99   
60144     352714  REP0207    1       69.99        69.99       79.98  59.99   
208709    471631  REP0134    1       69.99        69.99       79.98  59.99   
71429     362713  REP0208    1       69.99        69.99      129.96  59.99   
67249     358984  REP0207    1       69.99        69.99       79.98  59.99   
190304    458245  REP0060    1       39.91        39.91       49.90  29.99   
20839     318397  REP0060    1       39.91        39.91       49.90  29.99   
8178      307245  REP0060    1       39.91        39.91       49.90  29.99   
4374      303745  REP0151    1

Now I'm done with fixing the prices. After looking at all this stuff, I think that the total_paid is often times out of place. I should remove that column. Also I didn't fix the promo price. Since I am interested at the actual discount I won't need the promo_price, I only have to compare unit_price and price.
I will keep the price_diff column. Also I will look at a discount in percent.

When I will create different categories, I want to create a Second hand category!

I'm not sure if I want to keep desc and in_stock. Might be interesting to see, if discounts are not made if sth is out of stock. Not sure if I will look into that though

I will probably keep the desc for the categorization

In [44]:
orders_comp.drop(['promo_price', 'total_paid'], axis = 1, inplace=True)

In [45]:
orders_comp['disc_perc'] = (1 - orders_comp.unit_price / orders_comp.price)*100

# Filling last nan-values

Before categorizing things, I noticed that not all sku's have a brand. I will add the brand names to the orders_comp table. I found the names mostly by googling the name of the products.

In [46]:
orders_comp.loc[orders_comp.brand.isna()]

order_id        sku  qty  unit_price  total_price  price  \
1161      300660    par0072    1      199.00       199.00 349.00   
1589      301094    LEA0007    1       84.99        84.99  89.99   
5448      304785    MRL0008    1       45.99        45.99  59.99   
6813      306015    CAR0007    1       19.99        19.99  29.99   
8345      307405    LEA0007    1       84.99        84.99  89.99   
22485     319829  LEA0001-A    1       72.72        72.72  89.99   
27113     323918    MOO0008    1       49.99        49.99  79.95   
33960     329857    LEP0014    1       16.14        16.14  59.99   
57853     350588    HYN0007    4       68.69       274.76  74.99   
81167     371248    MRL0007    1      129.99       129.99 169.00   
85326     374843    MRL0007    1      129.99       129.99 169.00   
85461     374954    MRL0007    1      129.99       129.99 169.00   
93719     382260    SMR0007    1      189.99       189.99 199.00   
105428    392549    EXT0007    1      199.99       199.99 199.99   
137629    421028    COR0008    2      299.99       599.98 302.99   
185125    455592    TWI0008    1       59.99        59.99  69.99   
185953    456069    TWI0008    1       59.99        59.99  69.99   
186074    456182    TWI0008    2       59.99       119.98  69.99   
188566    457200    TWI0008    2       59.99       119.98  69.99   
189629    457804    TWI0008    1       59.99        59.99  69.99   
192775    459281    TWI0008    1       59.99        59.99  69.99   
202383    465846    UBT0007    1      349.95       349.95 349.99   
203214    466622    SMR0007    1      169.99       169.99 199.00   
204375    467626    TWI0008    2       59.99       119.98  69.99   
204461    467701    TWI0008    1       59.99        59.99  69.99   
205358    468513    TWI0008    1       59.99        59.99  69.99   
205508    468647    TWI0008    1       59.99        59.99  69.99   
212267    474840    UBT0008    1      197.95       197.95 219.95   
218212    480201    UBT0007    1      314.96       314.96 349.99   
218233    480220    UBT0007    1      349.95       349.95 349.99   
218539    480520    LUM0010    1       59.99        59.99  79.99   
236241    492009    par0072    2      209.99       419.98 349.00   
238072    420849    SMR0007    1      149.99       149.99 199.00   
253951    502848  WAH0002-A    1       39.00        39.00  79.99   
263853    508738    COR0010    1      129.99       129.99 131.99   
277433    519066    UBI0008    1      129.99       129.99 129.99   
283427    523397    UBI0007    1      359.99       359.99 359.99   
288642    526003    NET0028    1      404.99       404.99 429.99   

                                                     name          order_date  \
1161    Parrot AR Drone 2.0 Elite Edition cuadricópter... 2017-01-02 15:48:02   
1589               Leap Motion Sensor controller gestures 2017-01-02 22:40:02   
5448             Brown Marley Chant Mini Wireless Speaker 2017-01-08 14:29:15   
6813           Cardboard Safari Cardboard iPad TV Support 2017-01-09 19:53:46   
8345               Leap Motion Sensor controller gestures 2017-01-11 17:01:19   
22485       Open - Leap Motion Sensor Controller gestures 2017-02-04 12:36:27   
27113                 Now Moov Red Coach Activity Monitor 2017-02-14 08:40:24   
33960   Lepow USB 6000mAh External Battery Moonstone W... 2017-02-27 15:58:57   
57853                Mac memory DIMM DDR3 1066MHz 8GB FCM 2017-04-28 01:50:33   
81167           Get Together Midnight Marley Wood Speaker 2017-07-01 15:40:26   
85326           Get Together Midnight Marley Wood Speaker 2017-07-09 18:20:33   
85461           Get Together Midnight Marley Wood Speaker 2017-07-09 23:07:01   
93719                          SmartHalo GPS bike Backlit 2017-07-26 19:24:44   
105428          Extreme Fliers Micro Drone 3.0 Combo Pack 2017-08-25 00:59:58   
137629              Corning Optical Thunderbolt Cable 10m 2017-11-02 12:20:36   
185125              Pack 105 twinkly Christmas lights LED 2

In [47]:
orders_comp.loc[orders_comp.sku.str[:3] == 'COR', 'brand'] = 'Corning'
orders_comp.loc[orders_comp.sku.str[:3] == 'SMR', 'brand'] = 'SmartHalo' #insolvent btw
orders_comp.loc[orders_comp.sku.str[:3] == 'MRL', 'brand'] = 'House of Marley' #eco friendly music-boxes, keeping the legacy of bob marley's lov for music alive
orders_comp.loc[orders_comp.sku.str[:3] == 'LEP', 'brand'] = 'Lepow' #specialized in high-end mobile electronics, based in HK
orders_comp.loc[orders_comp.sku.str[:3] == 'MOO', 'brand'] = 'Moov' #music, audio service, but also fitness-watches and stuff
orders_comp.loc[orders_comp.sku.str[:3] == 'LEA', 'brand'] = 'Leap Motion' #controlling the notebook with motion, without touching, insolvent
orders_comp.loc[orders_comp.sku.str[:3] == 'CAR', 'brand'] = 'Cardboard Safari'#building animals out of wood, acryl, etc.
orders_comp.loc[orders_comp.sku.str[:3] == 'par', 'brand'] = 'Parrot' #french company, specializes on drones
orders_comp.loc[orders_comp.sku.str[:3] == 'WAH', 'brand'] = 'Wahoo Fitness'#american fitness-technology company
orders_comp.loc[orders_comp.sku.str[:3] == 'NET', 'brand'] = 'Netgear' #networking products
orders_comp.loc[orders_comp.sku.str[:3] == 'EXT', 'brand'] = 'Extreme Fliers'#micro-drones
orders_comp.loc[orders_comp.sku.str[:3] == 'TWI', 'brand'] = 'Twinkly'#italian smartphone controlled LED-lights producer
orders_comp.loc[orders_comp.sku.str[:3] == 'UBT', 'brand'] = 'Ubtech' #chinese company, humanoid robotics
orders_comp.loc[orders_comp.sku.str[:3] == 'LUM', 'brand'] = 'LuMee'#lighting company
orders_comp.loc[orders_comp.sku.str[:3] == 'UBI', 'brand'] = 'Ubiquity'#network components
orders_comp.loc[orders_comp.sku.str[:3] == 'HYN', 'brand'] = 'Hyundai Electronics'#second largest memory chipmaker, third largest semiconductor company

In [48]:
orders_comp.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 61322 entries, 6 to 289947
Data columns (total 13 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     61322 non-null  int64         
 1   sku          61322 non-null  object        
 2   qty          61322 non-null  int64         
 3   unit_price   61322 non-null  float64       
 4   total_price  61322 non-null  float64       
 5   price        61322 non-null  float64       
 6   name         61322 non-null  object        
 7   order_date   61322 non-null  datetime64[ns]
 8   brand        61322 non-null  object        
 9   desc         61318 non-null  object        
 10  in_stock     61322 non-null  int64         
 11  price_diff   61322 non-null  float64       
 12  disc_perc    61322 non-null  float64       
dtypes: datetime64[ns](1), float64(5), int64(3), object(4)
memory usage: 6.5+ MB


Looks almost good. Since I cannot find a fitting description for the 4 missing items, I just copy the name into it. By doing this I make sure that I can use string methods on the description column to find appropriate categories. Otherwise I'd get an error because of NaNs.

In [49]:
orders_comp.loc[orders_comp.desc.isna(), 'desc'] = orders_comp.loc[orders_comp.desc.isna(), 'name']

In [442]:
path = r'C:\Users\muell\Desktop\WBS\Project 2\coding_challenges\clean_csv'

SyntaxError: EOL while scanning string literal (Temp/ipykernel_12192/979721235.py, line 1)

In [443]:
orders_comp.to_csv(path + '\orders_comp.csv', index=False)

# Finding categories

Now let's move on to finding some categories for the products. To find those I'll combine the brand name with string methods (regex) on the name and description on the products. I'll group by brands to see which ones sold the most products. These will be the brands I focus on for now. Furthermore I'll probably want to set categories as well as subcategories.

In [324]:
orders_comp['category'] = 'other'
orders_comp['subcategory'] = 'other'

In [52]:
orders_comp.brand.value_counts()

Apple                  13827
OWC                     3607
Pack                    2550
Belkin                  2256
LaCie                   2091
Crucial                 2027
Satechi                 1891
Western Digital         1859
Wacom                   1812
NewerTech               1575
iFixit                  1516
SanDisk                 1126
Seagate                  872
Griffin                  841
Samsung                  797
LG                       770
ZaggKeys                 743
Tucano                   703
Otterbox                 657
Dell                     642
JBL                      587
Synology                 558
Lifeproof                539
Philips                  533
Matias                   529
Moshi                    495
FCM                      473
Startech                 468
Spek SeeThru             444
Logitech                 435
Bose                     414
Kingston                 397
Mophie                   397
Trascend                 395
Macally       

Ok, so Apple has by far the most products. Let's get an idea what Apple is selling here. For sorting out the categories, I will only use the cell below.

In [454]:
#(
#    orders_comp.loc[(orders_comp.brand == 'Apple')
#                    &(orders_comp.category=='other')].sort_values('price',ascending=False)
#)
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Apple Dock Connector'))].sort_values('price',ascending=False)
)

order_id      sku  qty  unit_price  total_price  price  \
8768      307793  APP0234    1       35.00        35.00  35.00   
17181     315086  APP0234    1       35.00        35.00  35.00   
115230    401268  AP20125    1        5.99         5.99  35.00   

                                          name          order_date  brand  \
8768               Apple Dock Connector to VGA 2017-01-12 10:03:01  Apple   
17181              Apple Dock Connector to VGA 2017-01-26 11:55:06  Apple   
115230  Like new - Apple Dock Connector to VGA 2017-09-20 13:41:10  Apple   

                              desc  in_stock  price_diff  disc_perc  \
8768    Dock Connector to VGA IOS.         0        0.00       0.00   
17181   Dock Connector to VGA IOS.         0        0.00       0.00   
115230   Dock Connector to VGA IOS         0       29.01      82.89   

               category subcategory  
8768    adapters_cables       other  
17181   adapters_cables       other  
115230  adapters_cables       other

In [474]:
# Prices for iphones start at about 400. All other iphone equipment is much cheaper. 
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    & (orders_comp.name.str.contains('iPhone'))
                    & (orders_comp.price > 300), 'category']
) = 'devices'
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    & (orders_comp.name.str.contains('iPhone'))
                    & (orders_comp.price > 300), 'subcategory']
) = 'apple_iphones'



In [475]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                   &(orders_comp.desc.str.contains('[Cc]ase')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                   &(orders_comp.desc.str.contains('[Cc]ase')), 'subcategory']
) = 'apple_iphone_cases'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                    &(orders_comp.name.str.contains('Apple'))
                    &(orders_comp.name.str.contains('Case'))
                   &(orders_comp.category != 'iphones'), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                    &(orders_comp.name.str.contains('Apple'))
                    &(orders_comp.name.str.contains('Case'))
                   &(orders_comp.category != 'iphones'), 'subcategory']
) = 'apple_iphone_cases'

In [476]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                    &(orders_comp.desc.str.contains('[Cc]onnector'))
                    &(orders_comp.desc.str.contains('[Dd]ock')),'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPhone'))
                    &(orders_comp.desc.str.contains('[Cc]onnector'))
                    &(orders_comp.desc.str.contains('[Dd]ock')),'subcategory']
) = 'apple_iphone_charging'

In [477]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    & (orders_comp.desc.str.contains('iPhone'))
                    & (orders_comp.desc.str.contains('Battery')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    & (orders_comp.desc.str.contains('iPhone'))
                    & (orders_comp.desc.str.contains('Battery')), 'subcategory']
) = 'apple_iphone_battery_cases'

In [478]:
# apple care products for extended warranty are easy to spot. I'll filter by the description.
# I just put them to service, which I'll divide into warranty and repair at least
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.desc.str.contains('extended warranty')), 'category']
) = 'service'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.desc.str.contains('extended warranty')), 'subcategory']
) = 'applecare_warranty'

In [479]:
# prices for macbooks are always above 500, regardless of new or used. 
# Might have to revisit, if the name is written somewhat else.
# Maybe I go for new and used as subcategories
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.name.str.contains('Mac[bB]ook|iMac|Mac Pro|Mac mini'))
                    &(orders_comp.price > 500), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.name.str.contains('Mac[bB]ook|iMac|Mac Pro|Mac mini'))
                    &(orders_comp.price > 500), 'subcategory']
) = 'apple_macbooks'

In [480]:
# MagSafe adapters. 20 of these entries are MagSafe 1 to MagSafe 2 converter
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('MagSafe')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('MagSafe')), 'subcategory']
) = 'apple_macbook_charging'

In [481]:
# ipads are above 250, nothing with iPad in the name is that expensive
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.name.str.contains('iPad'))
                    &(orders_comp.price > 250), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   & (orders_comp.name.str.contains('iPad'))
                    &(orders_comp.price > 250), 'subcategory']
) = 'apple_ipads'

In [482]:
# Apple Watches are above 250 before there is sth else
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('[Ww]atch'))
                   &(orders_comp.price > 250), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('[Ww]atch'))
                   &(orders_comp.price > 250), 'subcategory']
) = 'applewatch'

# Here come the charger for apple watches
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('Apple [Ww]atch'))
                    &(orders_comp.name.str.contains('[Mm]agnetic')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('Apple [Ww]atch'))
                    &(orders_comp.name.str.contains('[Mm]agnetic')), 'subcategory']
) = 'applewatch_charging'

# some straps that were missing
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Correa')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Correa')), 'subcategory']
) = 'applewatch_straps'

In [483]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Strap')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Strap')), 'subcategory']
) = 'applewatch_straps'

In [484]:
# AirPorts are a thing apparently
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                  &(orders_comp.name.str.contains('Air[Pp]ort')), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                  &(orders_comp.name.str.contains('Air[Pp]ort')), 'subcategory']
) = 'apple_airports'

In [485]:
# I only saw ipod touch, nano and shuffle. By specifying in the regex, I don't need a price range
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('iPod Touch|iPod Shuffle|iPod Nano')), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                   &(orders_comp.name.str.contains('iPod Touch|iPod Shuffle|iPod Nano')), 'subcategory']
) = 'apple_ipods'

In [486]:
# apple tv products cost at least above 70. Cheaper products are warranty products
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Apple TV'))
                    &(orders_comp.price > 75), 'category']
) = 'devices'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Apple TV'))
                    &(orders_comp.price > 75), 'subcategory']
) = 'appletv'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Siri|Remote Loop')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Siri|Remote Loop')), 'subcategory']
) = 'appletv_remote'

In [487]:
# Since the smart keyboards /smart cover | Apple Pencils are designed for ipads, I will put them in that category. 
# Might have to change category name later
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Smart Keyboard|iPad Keyboard|Smart Cover|Pencil')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Smart Keyboard|iPad Keyboard')), 'subcategory']
) = 'apple_ipad_keyboards'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Smart Cover')), 'subcategory']
) = 'apple_ipad_cases'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Pencil')), 'subcategory']
) = 'apple_ipad_pencils'

In [488]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPad'))
                    &(orders_comp.name.str.contains('Case')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('iPad'))
                    &(orders_comp.name.str.contains('Case')), 'subcategory']
) = 'apple_ipad_cases'

In [489]:
# I put earpods and airpods in one category
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('AirPods|EarPods|Headphones')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('AirPods')), 'subcategory']
) = 'apple_headphones_airpods'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('EarPods')), 'subcategory']
) = 'apple_headphones_earpods'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Headphones'))
                    &(~orders_comp.name.str.contains('Airpods'))
                    &(~orders_comp.name.str.contains('Earpods')), 'subcategory']
) = 'apple_headphones'

In [490]:
# Man I didn't know how much stuff Apple has. 
# There is a MacBook which contains 'Magic', therefore I add a price limit for magic products
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Magic'))
                    &(orders_comp.price < 200), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Magic'))
                    &(orders_comp.name.str.contains('[Mm]ouse'))
                    &(orders_comp.price < 200), 'subcategory']
) = 'apple_magic_mouse'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Magic'))
                    &(orders_comp.name.str.contains('[Tt]rackpad'))
                    &(orders_comp.price < 200), 'subcategory']
) = 'apple_magic_trackpad'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Magic'))
                    &(orders_comp.name.str.contains('[Kk]ey[Bb]oard'))
                    &(orders_comp.price < 200), 'subcategory']
) = 'apple_magic_keyboard'

In [491]:
# fortunately every entry containing '[aA]datper' is really an adapter it seems.
# I hope this doesn't include chargers ---> it doesn't :)
# 


(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Aa]dapter|Apple Dock Connector')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Aa]dapter|Apple Dock Connector')), 'subcategory']
) = 'apple_adapters_cables'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.desc.str.contains('[Aa]dapter')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.desc.str.contains('[Aa]dapter')), 'subcategory']
) = 'apple_adapters_cables'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Cc]able'))
                    &(~orders_comp.name.str.contains('[Mm]agnetic')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Cc]able'))
                    &(~orders_comp.name.str.contains('[Mm]agnetic')), 'subcategory']
) = 'apple_adapters_cables'

In [492]:
# Now I start my accessories category. 
#I'll use it for stuff that can be used not for apple products and that are more like gadgets
(    
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Ss]uper[Dd]rive')), 'category']
) = 'accessories'

(    
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Ss]uper[Dd]rive')), 'subcategory']
) = 'apple_superdrive'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Keypad'))
                   &(~orders_comp.name.str.contains('Magic')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Keypad'))
                   &(~orders_comp.name.str.contains('Magic')), 'subcategory']
) = 'apple_keyboard'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Wireless'))
                    &(orders_comp.name.str.contains('Keyboard')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Wireless'))
                    &(orders_comp.name.str.contains('Keyboard')), 'subcategory']
) = 'apple_keyboard'

(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Mm]ouse'))
                   &(~orders_comp.name.str.contains('Magic')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('[Mm]ouse'))
                   &(~orders_comp.name.str.contains('Magic')), 'subcategory']
) = 'apple_mouse'

In [493]:
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Belt Loop')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Apple')
                    &(orders_comp.name.str.contains('Belt Loop')), 'subcategory']
) = 'other'

Apple done, now OWC

In [621]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                    &(orders_comp.category =='other')
                #   &(orders_comp.desc.str.contains('Kit temperature'))
              #      &(orders_comp.name.str.contains('[Kk]it'))
                #    &(orders_comp.name.str.contains('Case'))
                   ].sort_values('price', ascending=False)
)

Empty DataFrame
Columns: [order_id, sku, qty, unit_price, total_price, price, name, order_date, brand, desc, in_stock, price_diff, disc_perc, category, subcategory]
Index: []

In [682]:
# lot of superdrives

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('[Oo]ptical')), 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('[Oo]ptical')), 'subcategory']
) = 'superdrives'

In [616]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('RAM|Aluminium housing|Aluminum housing')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('RAM|Aluminium housing|Aluminum housing')), 'subcategory']
) = 'computer_parts'

In [605]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('[Hh]ard [Dd]rive'))
                    &(~orders_comp.name.str.contains('[Oo]ptical'))
                    &(~orders_comp.name.str.contains('[Aa]dapter'))
                   , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('[Hh]ard [Dd]rive'))
                    &(~orders_comp.name.str.contains('[Oo]ptical'))
                    &(~orders_comp.name.str.contains('[Aa]dapter'))
                   , 'subcategory']
) = 'computer_parts'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('SSD'))
                    &(orders_comp.desc.str.contains('\d+GB|\d+TB'))
                   , 'category']
) ='accessories'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('SSD'))
                    &(orders_comp.desc.str.contains('\d+GB|\d+TB'))
                   , 'subcategory']
) ='computer_parts'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('ThunderBay'))
                   ,'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('ThunderBay'))
                   ,'subcategory']
) = 'computer_parts'

In [606]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('Dock'))
                   ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('Dock'))
                   ,'subcategory']
) = 'adapters_cables'

In [607]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('DDR\d|memory|Thunderbolt|RAID'))
                   , 'category']
) ='accessories'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                    &(orders_comp.category =='other')
                   &(orders_comp.name.str.contains('DDR\d|memory|Thunderbolt|RAID'))
                    &(~orders_comp.name.str.contains('[Cc]able'))
                   , 'subcategory']
) = 'computer_parts'

(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                    &(orders_comp.category =='other')
                   &(orders_comp.name.str.contains('DDR\d|memory|Thunderbolt|RAID'))
                    &(orders_comp.name.str.contains('[Cc]able'))
                   , 'subcategory']
) = 'adapters_cables'

In [608]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                    &(~orders_comp.desc.str.contains('[Rr]eplacement|[Ss]ubstitution'))
                    &(orders_comp.name.str.contains('[Aa]dapter'))
                    , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                    &(~orders_comp.desc.str.contains('[Rr]eplacement|[Ss]ubstitution'))
                    &(orders_comp.name.str.contains('[Aa]dapter'))
                    , 'subcategory']
) = 'adapters_cables'

In [609]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('SSD'))
                    &(orders_comp.name.str.contains('Case'))
                    &(orders_comp.price < 1000)
                   , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('SSD'))
                    &(orders_comp.name.str.contains('Case'))
                    &(orders_comp.price < 1000)
                   , 'subcategory']
) = 'cases'

In [617]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('[Ii]nstallation|shielding'))
                    &(orders_comp.name.str.contains('[Kk]it'))
                   , 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('[Ii]nstallation'))
                    &(orders_comp.name.str.contains('[Kk]it'))
                   , 'subcategory']
) = 'installation_kit'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('shielding'))
                    &(orders_comp.name.str.contains('[Kk]it'))
                   , 'subcategory']
) = 'shielding_kit'

In [611]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('raid', case=False)), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.name.str.contains('raid', case=False)), 'subcategory']
) = 'computer_parts'

In [612]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('repair', case=False))
                   , 'category']
) ='tools'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('repair', case=False))
                   , 'subcategory']
) ='repair_kit'

In [613]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')

                   &(orders_comp.desc.str.contains('Box Portable|outer case|Outer carton|External Case|External SSD box')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')

                   &(orders_comp.desc.str.contains('Box Portable|outer case|Outer carton|External Case|External SSD box')), 'subcategory']
) = 'cases'


In [620]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('Kit temperature|[tT]emperature sensor|internal disk reading')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('Kit temperature|[Tt]emperature sensor|internal disk reading')), 'subcategory']
) = 'computer_parts'

In [619]:
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('PCI Express')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'OWC')
                   &(orders_comp.desc.str.contains('PCI Express')), 'subcategory']
) = 'adapters_cables'

In [693]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.category=='other')
               #     &(orders_comp.desc.str.contains('[Ee]xternal [Hh]ard [Dd]rive'))
                 #   &(orders_comp.desc.str.contains('[Ee]xpansion|[Uu]pgrade'))
                   ].sort_values('price', ascending=False).info()
                  #  &(orders_comp.price <414)].sort_values('price', ascending=False).head(100)
                 #   &(orders_comp.name.str.contains('Apple i?Mac'))].sort_values('price', ascending=False).tail(100)
                  # &(orders_comp.desc.str.contains('PCI Express')), 'category']
)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 115 entries, 171802 to 505
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     115 non-null    int64         
 1   sku          115 non-null    object        
 2   qty          115 non-null    int64         
 3   unit_price   115 non-null    float64       
 4   total_price  115 non-null    float64       
 5   price        115 non-null    float64       
 6   name         115 non-null    object        
 7   order_date   115 non-null    datetime64[ns]
 8   brand        115 non-null    object        
 9   desc         115 non-null    object        
 10  in_stock     115 non-null    int64         
 11  price_diff   115 non-null    float64       
 12  disc_perc    115 non-null    float64       
 13  category     115 non-null    object        
 14  subcategory  115 non-null    object        
dtypes: datetime64[ns](1), float64(5), int64(3), object(6

In [658]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.name.str.contains('DS\d+')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.name.str.contains('DS\d+')), 'subcategory']
) = 'servers'

(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('Apple i?Mac|iPhone')),'category']
) = 'devices'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('Apple i?Mac')),'subcategory']
) = 'apple_macbooks'

(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('iPhone')),'subcategory']
) = 'apple_iphones'

In [689]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.name.str.contains('Cinema Display|ThunderBay')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.name.str.contains('Cinema Display')), 'subcategory']
) = 'monitors'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.name.str.contains('Cinema Display')), 'subcategory']
) = 'computer_parts'

(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.desc.str.contains('NAS|QNAP|WD My Cloud')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.desc.str.contains('NAS|QNAP|WD My Cloud')), 'subcategory']
) = 'servers'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.desc.str.contains('RAID|SSD upgrade|[Ee]xternal [Hh]ard [Dd]rive')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                   &(orders_comp.desc.str.contains('RAID|SSD upgrade|[Ee]xternal [Hh]ard [Dd]rive')), 'subcategory']
) = 'computer_parts'

In [661]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
             #       &(orders_comp.category=='other')
                    &(orders_comp.desc.str.contains('SSD'))
                    &(orders_comp.desc.str.contains('[Ee]xpansion|[Uu]pgrade'))
                   , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
             #       &(orders_comp.category=='other')
                    &(orders_comp.desc.str.contains('SSD'))
                    &(orders_comp.desc.str.contains('[Ee]xpansion|[Uu]pgrade'))
                   , 'subcategory']
) = 'computer_parts'

In [665]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('[Hh]eadset')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('[Hh]eadset')), 'subcategory']
) = 'headsets'

In [691]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('[Cc]able|[Cc]harger')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('[Cc]able|[Cc]harger')), 'subcategory']
) = 'adapters_cables'

In [674]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('Crucial')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('Crucial')), 'subcategory']
) = 'computer_parts'

In [677]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('[Ff]ixit')), 'category']
) = 'tools'

(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.name.str.contains('[Ff]ixit')), 'subcategory']
) = 'opening_tools'

In [683]:
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('Replacement')), 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'Pack')
                    &(orders_comp.desc.str.contains('Replacement')), 'subcategory']
) = 'superdrives'

Trying to work a little faster now. Will not categorize EVERY item anymore.

In [774]:
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                     &(orders_comp.category =='other')
             #      &(orders_comp.desc.str.contains('External Battery'))
         #          &(orders_comp.name.str.contains('Screen Protector'))
                 #   &(orders_comp.desc.str.contains('[Cc]ase'))
                  ].sort_values('price', ascending=False).head(100)
)

order_id        sku  qty  unit_price  total_price  price  \
250714    500847    BEL0180    1      119.99       119.99 149.99   
201091    464726    BEL0175    1       79.99        79.99  79.99   
262286    506488    BEL0367    1       55.99        55.99  59.99   
205522    468658    BEL0367    1       55.99        55.99  59.99   
253414    502477    BEL0367    1       55.99        55.99  59.99   
164945    443814    BEL0070    1       25.49        25.49  49.99   
226302    485701    BEL0070    1       29.99        29.99  49.99   
201939    465469    BEL0070    1       29.99        29.99  49.99   
58761     351467    BEL0070    1       29.99        29.99  49.99   
29356     325760    BEL0070    1       25.49        25.49  49.99   
153216    433890    BEL0219    1       22.94        22.94  29.99   
141025    423956    BEL0233    1       26.99        26.99  29.99   
216951    479042    BEL0219    1       25.64        25.64  29.99   
118750    404414    BEL0233    1       26.99        26.99  29.99   
121894    407183    BEL0219    1       25.64        25.64  29.99   
204381    467319    BEL0219    1       26.98        26.98  29.99   
131168    415457    BEL0219    1       26.99        26.99  29.99   
97148     385328    BEL0219    1       26.99        26.99  29.99   
87653     311688    BEL0233    1       26.99        26.99  29.99   
142713    424959    BEL0219    1       24.29        24.29  29.99   
157555    438240    BEL0219    1       22.94        22.94  29.99   
56903     349662    BEL0233    1       26.99        26.99  29.99   
149989    431982    BEL0233    1       29.99        29.99  29.99   
64212     356230    BEL0219    1       26.99        26.99  29.99   
152127    433682    BEL0219    1       22.94        22.94  29.99   
218550    480532    BEL0177    1       29.99        29.99  29.99   
68666     360238    BEL0233    1       26.99        26.99  29.99   
161551    435866    BEL0233    1       25.49        25.49  29.99   
21199     318709    BEL0233    1       26.99        26.99  29.99   
97354     385497    BEL0219    1       26.99        26.99  29.99   
6932      306122    BEL0233    1       26.99        26.99  29.99   
4919      304278  BEL0227-A    1       19.28        19.28  29.99   
282154    522388    BEL0233    1       29.99        29.99  29.99   
15001     313243    BEL0258    1       22.99        22.99  29.99   
236223    491990    BEL0219    1       26.99        26.99  29.99   
12912     311476    BEL0233    1       26.99        26.99  29.99   
17110     315024    BEL0219    2       26.99        53.98  29.99   
1157      300656    BEL0233    1       26.99        26.99  29.99   
13957     312359    BEL0219    4       25.64       102.56  29.99   
153962    435172    BEL0310    1       16.99        16.99  24.99   
144204    426817    BEL0310    1       19.99        19.99  24.99   
274061    504242    BEL0310    1       19.99        19.99  24.99   
157150    437903    BEL0310    1       16.99        16.99  24.99   
279421    520567    BEL0266    2       19.99        39.98  24.99   
157524    438263    BEL0310    1       16.99        16.99  24.99   
146223    428546    BEL0266    1       19.99        19.99  24.99   
145269    427735    BEL0310    1       19.99        19.99  24.99   
219036    480972    BEL0244    1       20.99        20.99  24.99   
143569    422891    BEL0172    1       14.99        14.99  24.99   
269058    512586    BEL0310    1       19.99        19.99  24.99   
282332    522533    BEL0310    1       19.99        19.99  24.99   
140255    423311    BEL0310    1       19.99        19.99  24.99   
283140    523176    BEL0310    1       19.99        19.99  24.99   
137023    420497    BEL0266    1       16.52        16.52  24.99   
286566    524792    BEL0244    1       20.99        20.99  24.99   
105276    392412    BEL0244    1       20.99        20.99  24.99   
101314    388941    BEL0171    1       24.99        24.99  24.99   
157542    438079    BEL0244    1       17.84        17.84  24.99

In [768]:
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                #    &(orders_comp.category =='other')
                   &(orders_comp.name.str.contains('PowerHouse'))
              #      &(orders_comp.name.str.contains('[Kk]it'))
                #    &(orders_comp.name.str.contains('Case'))
                   , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                #    &(orders_comp.category =='other')
                   &(orders_comp.name.str.contains('PowerHouse'))
              #      &(orders_comp.name.str.contains('[Kk]it'))
                #    &(orders_comp.name.str.contains('Case'))
                   , 'subcategory']
) = 'adapters_cables'

(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.name.str.contains('Screen Protector|Bandolier|[Aa]dapter|[Cc]harger|[Cc]able|Thunderbolt|RockStar MIXIT|Wireless charging|Backpack|Insight Power Control')), 'category']
) = 'accessories'

(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.name.str.contains('Screen Protector|Bandolier|Backpack')), 'subcategory']
) = 'cases'
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.name.str.contains('[Aa]dapter|[Cc]harger|[Cc]able|Thunderbolt|RockStar MIXIT|Wireless charging')), 'subcategory']
) = 'adapters_cables'

(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.name.str.contains('Insight Power Control')), 'subcategory']
) = 'gadgets'


In [772]:
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.desc.str.contains('[Cc]ase|[eE]xternal [Bb]attery|Loading dock|Charging Dock|[Cc]over|armband|controller|Keypad')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.desc.str.contains('Loading dock|Charging Dock')), 'subcategory']
) = 'adapters_cables'
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.desc.str.contains('[Cc]over|[Cc]ase|')), 'subcategory']
) = 'cases'
(
    orders_comp.loc[(orders_comp.brand == 'Belkin')
                   &(orders_comp.desc.str.contains('[eE]xternal [bB]attery|armband|controller|Keypad')), 'subcategory']
) = 'gadgets'

In [784]:
(
    orders_comp.loc[(orders_comp.brand == 'LaCie')
                     &(orders_comp.category =='other')
                 #  &(orders_comp.desc.str.contains('[Hh]ard [Dd]rive'))
         #          &(orders_comp.name.str.contains('Screen Protector'))
                 #   &(orders_comp.desc.str.contains('[Cc]ase'))
                  ].sort_values('price', ascending=False).head(100)
)

order_id      sku  qty  unit_price  total_price  price  \
50004    343683  LAC0107    1       49.99        49.99  69.99   

                                       name          order_date  brand  \
50004  LaCie 32GB USB 3.0 PenDrive XtremKey 2017-04-05 17:31:04  LaCie   

                                                    desc  in_stock  \
50004  32GB USB 3.0 flash drive resistant to extreme ...         0   

       price_diff  disc_perc category subcategory  
50004       20.00      28.58    other       other

In [786]:
(
    orders_comp.loc[(orders_comp.brand == 'LaCie')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'LaCie')
                   &(orders_comp.desc.str.contains('[Hh]ard [Dd]rive|Thunderbolt|RAID|Hard [Dd]isk'))
                  , 'subcategory']
) = 'computer_parts'
(
    orders_comp.loc[(orders_comp.brand == 'LaCie')
                   &(orders_comp.desc.str.contains('flash drive resistant'))
                  , 'subcategory']
) = 'flash_drive'

In [787]:
orders_comp.brand.value_counts()

Apple                  13827
OWC                     3607
Pack                    2550
Belkin                  2256
LaCie                   2091
Crucial                 2027
Satechi                 1891
Western Digital         1859
Wacom                   1812
NewerTech               1575
iFixit                  1516
SanDisk                 1126
Seagate                  872
Griffin                  841
Samsung                  797
LG                       770
ZaggKeys                 743
Tucano                   703
Otterbox                 657
Dell                     642
JBL                      587
Synology                 558
Lifeproof                539
Philips                  533
Matias                   529
Moshi                    495
FCM                      473
Startech                 468
Spek SeeThru             444
Logitech                 435
Bose                     414
Kingston                 397
Mophie                   397
Trascend                 395
Macally       

In [792]:
(
    orders_comp.loc[(orders_comp.brand == 'Crucial')
                     &(orders_comp.category =='other')
                   &(orders_comp.price<98)
         #          &(orders_comp.name.str.contains('Screen Protector'))
                 #   &(orders_comp.desc.str.contains('[Cc]ase'))
                  ].sort_values('price', ascending=False).head(500)
)

order_id        sku  qty  unit_price  total_price  price  \
130771    415104  CRU0025-2    1       90.99        90.99  97.98   
61374     353787  CRU0025-2    1       78.99        78.99  97.98   
136397    420001  CRU0025-2    1       90.99        90.99  97.98   
138632    421907  CRU0025-2    1       90.99        90.99  97.98   
141631    424529  CRU0025-2    1       80.07        80.07  97.98   
27130     323935  CRU0025-2    1       82.99        82.99  97.98   
17007     314933  CRU0025-2    1       65.69        65.69  97.98   
157213    438008  CRU0025-2    1       77.34        77.34  97.98   
264726    509282  CRU0025-2    1       90.99        90.99  97.98   
165130    443955  CRU0025-2    1       77.34        77.34  97.98   
18186     316012  CRU0025-2    1       72.99        72.99  97.98   
18587     316349  CRU0025-2    1       72.99        72.99  97.98   
170378    447859  CRU0025-2    1       77.34        77.34  97.98   
19714     317403  CRU0025-2    1       69.34        69.34  97.98   
170549    447825  CRU0025-2    2       77.34       154.68  97.98   
171131    448350  CRU0025-2    1       77.34        77.34  97.98   
171347    448518  CRU0025-2    1       77.34        77.34  97.98   
260063    506436  CRU0025-2    1       90.99        90.99  97.98   
171698    448820  CRU0025-2    1       77.34        77.34  97.98   
256991    504827  CRU0025-2    1       90.99        90.99  97.98   
172593    449501  CRU0025-2    1       77.34        77.34  97.98   
52572     345908  CRU0025-2    1       78.99        78.99  97.98   
180186    453185  CRU0025-2    1       90.99        90.99  97.98   
183919    454974  CRU0025-2    1       90.99        90.99  97.98   
253840    502755  CRU0025-2    1       90.99        90.99  97.98   
203311    466703  CRU0025-2    1       90.99        90.99  97.98   
206428    469536  CRU0025-2    1       81.99        81.99  97.98   
248011    499417  CRU0025-2    1       90.99        90.99  97.98   
213520    475955  CRU0025-2    1       81.99        81.99  97.98   
271959    514722  CRU0025-2    1       75.20        75.20  97.98   
151072    432907  CRU0025-2    1       77.34        77.34  97.98   
245468    497791  CRU0025-2    1       90.99        90.99  97.98   
123715    408875  CRU0025-2    1       78.99        78.99  97.98   
3758      301102  CRU0025-2    1      136.87       136.87  97.98   
102226    389695  CRU0025-2    1       78.99        78.99  97.98   
102667    390096  CRU0025-2    1       78.99        78.99  97.98   
279809    520882  CRU0025-2    1       90.99        90.99  97.98   
94592     383025  CRU0025-2    1       78.99        78.99  97.98   
110501    397020  CRU0025-2    1       78.99        78.99  97.98   
273408    515905  CRU0025-2    1       90.99        90.99  97.98   
7700      306824  CRU0025-2    1       72.99        72.99  97.98   
278557    519925  CRU0025-2    1       90.99        90.99  97.98   
278540    519910  CRU0025-2    1       90.99        90.99  97.98   
87860     376976  CRU0025-2    1       65.28        65.28  97.98   
123530    408696  CRU0025-2    1       78.99        78.99  97.98   
11693     310435  CRU0025-2    1       72.99        72.99  97.98   
84710     374328  CRU0025-2    1       65.28        65.28  97.98   
127518    412208  CRU0025-2    1       78.99        78.99  97.98   
128480    413047  CRU0025-2    1       90.99        90.99  97.98   
12677     311292  CRU0025-2    1       72.99        72.99  97.98   
273500    515991  CRU0025-2    1       90.99        90.99  97.98   
130044    414275  CRU0025-2    1       90.99        90.99  97.98   
97084     385272  CRU0025-2    1       78.99        78.99  97.98   
14024     312414  CRU0044-A    1       77.86        77.86  91.99   
190336    458278    CRU0049    2       91.36       182.72  91.36   
210711    473345    CRU0049    6       82.22       493.32  91.36   
84684     374304    CRU0049    1       64.99        64.99  91.36   
213691    476105    CRU0049    4       82.22       328.88  91.36

In [793]:
(
    orders_comp.loc[(orders_comp.brand == 'Crucial'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Crucial'), 'subcategory']
) = 'computer_parts_memory'


In [845]:
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                     &(orders_comp.subcategory =='other')
            #       &(orders_comp.price<79)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False)
)

Empty DataFrame
Columns: [order_id, sku, qty, unit_price, total_price, price, name, order_date, brand, desc, in_stock, price_diff, disc_perc, category, subcategory]
Index: []

In [835]:
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('[Hh]ub'))
                  , 'subcategory']
) = 'hubs'
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('Keypad'))
                  , 'subcategory']
) = 'keyboards'
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('[Hh]eadset|[Hh]eadphones|[Ee]arphones'))
                  , 'subcategory']
) = 'headphones'
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('[Ss]peakers'))
                  , 'subcategory']
) = 'speakers'

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('Mac'))
                    &(orders_comp.desc.str.contains('[Ss]tand')), 'subcategory']
) = 'macbook_stands'

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('[Cc]able')), 'subcategory']
) = 'adapters_cables'

In [844]:

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('Outer carton|External box')), 'subcategory']
) = 'cases'

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('[Dd]ock|charging|Card reader')), 'subcategory']
) = 'adapters_cables'



In [827]:

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('[Ss]upport')), 'subcategory']
) = 'support'


(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('[Ss]upport')), 'subcategory']
) = 'support'

In [820]:

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('[Aa]dapter|[Cc]harger')), 'subcategory']
) = 'adapters_cables'

In [840]:

(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('Aluminum mat|mat aluminum')), 'subcategory']
) = 'mouse_mat'
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.desc.str.contains('briefcase')), 'subcategory']
) = 'macbook_cases'

In [842]:
(
    orders_comp.loc[(orders_comp.brand == 'Satechi')
                   &(orders_comp.name.str.contains('Power Meter|Multimedia')), 'subcategory']
) = 'gadgets'

In [846]:
orders_comp.brand.value_counts()

Apple                  13827
OWC                     3607
Pack                    2550
Belkin                  2256
LaCie                   2091
Crucial                 2027
Satechi                 1891
Western Digital         1859
Wacom                   1812
NewerTech               1575
iFixit                  1516
SanDisk                 1126
Seagate                  872
Griffin                  841
Samsung                  797
LG                       770
ZaggKeys                 743
Tucano                   703
Otterbox                 657
Dell                     642
JBL                      587
Synology                 558
Lifeproof                539
Philips                  533
Matias                   529
Moshi                    495
FCM                      473
Startech                 468
Spek SeeThru             444
Logitech                 435
Bose                     414
Kingston                 397
Mophie                   397
Trascend                 395
Macally       

In [851]:
(
    orders_comp.loc[(orders_comp.brand == 'Western Digital')
                     &(orders_comp.category =='other')
                    &(orders_comp.price<60)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False).head(500)
)

order_id        sku  qty  unit_price  total_price  price  \
93852    382405  WDT0135-A    2       11.84        23.68  12.90   

                                                    name          order_date  \
93852  Open - Western Digital Network PC and Mac 3TB ... 2017-07-26 17:04:47   

                 brand                                               desc  \
93852  Western Digital  Open WD hard drive in perfect condition design...   

       in_stock  price_diff  disc_perc category subcategory  
93852         0        1.06       8.22    other       other

In [853]:
(
    orders_comp.loc[(orders_comp.brand == 'Western Digital'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Western Digital'), 'subcategory']
) = 'computer_parts_memory'
(
    orders_comp.loc[(orders_comp.brand == 'Western Digital')
                    &(orders_comp.desc.str.contains('NAS'))
                    &(~orders_comp.desc.str.contains('[Hh]ard [Dd]rive')), 'subcategory']
) = 'servers'

In [876]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                     &(orders_comp.category =='other')
                 #   &(orders_comp.price<60)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False).head(500)
)

order_id        sku  qty  unit_price  total_price  price  \
15637    313775  WAC0170-A    1       78.93        78.93 159.90   
16518    314517  WAC0170-A    1       78.93        78.93 159.90   
23832    321012    WAC0176    1       79.99        79.99 159.90   
25531    322514    WAC0176    1       79.99        79.99 159.90   
19482    317195  WAC0175-A    1       35.30        35.30  59.90   

                                                  name          order_date  \
15637  Open - Wacom Bamboo Spark snap-fit ​​iPad Air 2 2017-01-23 13:24:25   
16518  Open - Wacom Bamboo Spark snap-fit ​​iPad Air 2 2017-01-25 00:39:46   
23832         Wacom Bamboo Spark snap-fit ​​iPad Air 2 2017-02-07 17:14:24   
25531         Wacom Bamboo Spark snap-fit ​​iPad Air 2 2017-02-11 08:51:19   
19482      Open - Wacom Bamboo Fineline 2 Pointer Gold 2017-01-30 09:40:13   

       brand                                          desc  in_stock  \
15637  Wacom                             Bloc Smart notes.         0   
16518  Wacom                             Bloc Smart notes.         0   
23832  Wacom                             Bloc Smart notes.         0   
25531  Wacom                             Bloc Smart notes.         0   
19482  Wacom  Intelligent digital thin pencil tip for iPad         0   

       price_diff  disc_perc category subcategory  
15637       80.97      50.64    other       other  
16518       80.97      50.64    other       other  
23832       79.91      49.97    other       other  
25531       79.91      49.97    other       other  
19482       24.60      41.07    other       other

In [862]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Gg]raphics? [Tt]ablet|Graphical touch tablet')), 'category']
) = 'devices'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Gg]raphics? [Tt]ablet|Graphical touch tablet')), 'subcategory']
) = 'graphics_tablet'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('[Gg]raphics? [Tt]ablet|Graphical touch tablet')), 'category']
) = 'devices'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('[Gg]raphics? [Tt]ablet|Graphical touch tablet')), 'subcategory']
) = 'graphics_tablet'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Gg]raphics? [Dd]isplay')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Gg]raphics? [Dd]isplay')), 'subcategory']
) = 'graphic_display_macbook'

In [867]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains(' [Pp]en |[Pp]ointer|[Ss]tylus'))
                    &(~orders_comp.desc.str.contains('[Rr]eplacement'))
                    &(~orders_comp.name.str.contains('Folio|Slate')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains(' [Pp]en |[Pp]ointer|[Ss]tylus'))
                    &(~orders_comp.desc.str.contains('[Rr]eplacement'))
                    &(~orders_comp.name.str.contains('Folio|Slate')), 'subcategory']
) = 'tablet_pencils'

In [870]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains(' [Pp]en |[Pp]ointer|[Ss]tylus|tips'))
                    &(orders_comp.desc.str.contains('[Rr]eplacement'))
                    &(~orders_comp.name.str.contains('Folio|Slate')), 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains(' [Pp]en |[Pp]ointer|[Ss]tylus|tips'))
                    &(orders_comp.desc.str.contains('[Rr]eplacement'))
                    &(~orders_comp.name.str.contains('Folio|Slate')), 'subcategory']
) = 'tablet_pencils'

In [871]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('Bloc'))
                    &(orders_comp.name.str.contains('Slate')), 'category']
) = 'devices'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('Bloc'))
                    &(orders_comp.name.str.contains('Slate')), 'subcategory']
) = 'notepads'

In [872]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('Folio')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('Folio')), 'subcategory']
) = 'tablet_cases'

In [874]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Ss]upport')), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.desc.str.contains('[Ss]upport')), 'subcategory']
) = 'tablet_support'

In [875]:
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('Accessory Kit')), 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'Wacom')
                    &(orders_comp.name.str.contains('Accessory Kit')), 'subcategory']
) = 'tablet_pencil_tools'

In [892]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                     &(orders_comp.category =='other')
                  #  &(orders_comp.price<29)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False).info()
)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 55 entries, 63324 to 566
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     55 non-null     int64         
 1   sku          55 non-null     object        
 2   qty          55 non-null     int64         
 3   unit_price   55 non-null     float64       
 4   total_price  55 non-null     float64       
 5   price        55 non-null     float64       
 6   name         55 non-null     object        
 7   order_date   55 non-null     datetime64[ns]
 8   brand        55 non-null     object        
 9   desc         55 non-null     object        
 10  in_stock     55 non-null     int64         
 11  price_diff   55 non-null     float64       
 12  disc_perc    55 non-null     float64       
 13  category     55 non-null     object        
 14  subcategory  55 non-null     object        
dtypes: datetime64[ns](1), float64(5), int64(3), object(6)


In [880]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Dd]ock|[Aa]dapter|[Cc]able'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Dd]ock|[Aa]dapter|[Cc]able'))
                  , 'subcategory']
) = 'adapters_cables'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.name.str.contains('[Dd]ock|[Aa]dapter|[Cc]able'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.name.str.contains('[Dd]ock|[Aa]dapter|[Cc]able'))
                  , 'subcategory']
) = 'adapters_cables'

In [890]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('storage box'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('storage box'))
                  , 'subcategory']
) = 'cases'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Ii]Phone'))
                    &(orders_comp.desc.str.contains('[Cc]ase|casing'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Ii]Phone'))
                    &(orders_comp.desc.str.contains('[Cc]ase|casing'))
                  , 'subcategory']
) = 'iphone_cases'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('[Ii]Phone'))
                    &(orders_comp.name.str.contains('[Cc]ase'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('[Ii]Phone'))
                    &(orders_comp.name.str.contains('[Cc]ase'))
                  , 'subcategory']
) = 'iphone_cases'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('[Ii]Pad'))
                    &(orders_comp.name.str.contains('[Cc]ase'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('[Ii]Pad'))
                    &(orders_comp.name.str.contains('[Cc]ase'))
                  , 'subcategory']
) = 'ipad_cases'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Pp]rotector'))
                    &(orders_comp.desc.str.contains('MacBook'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Pp]rotector'))
                    &(orders_comp.desc.str.contains('MacBook'))
                  , 'subcategory']
) = 'macbook_cases'

In [882]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('Kit tools'))
                  , 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.name.str.contains('Kit tools'))
                  , 'subcategory']
) = 'tools'

In [883]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('MacBook'))
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  , 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('MacBook'))
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  , 'subcategory']
) = 'macbook_battery'

In [888]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Hh]ousing|Raid'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('[Hh]ousing|Raid'))
                  , 'subcategory']
) = 'computer_parts'

In [889]:
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('Elegant'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'NewerTech')
                   &(orders_comp.desc.str.contains('Elegant'))
                  , 'subcategory']
) = 'macbook_support'

In [898]:
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                     &(orders_comp.category =='other')
                   # &(orders_comp.price<39)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False).head(500)
)

order_id      sku  qty  unit_price  total_price  price  \
134355    418251  IFX0136    1       89.99        89.99  89.95   
203611    466951  IFX0136    1       89.99        89.99  89.95   
276753    518471  IFX0136    1       85.49        85.49  89.95   
1008      300518  IFX0136    1       89.99        89.99  89.95   
4022      303394  IFX0136    2       89.99       179.98  89.95   
256818    504676  IFX0136    1       85.49        85.49  89.95   
193411    459616  IFX0136    1       89.99        89.99  89.95   
56112     348964  IFX0038    1       79.99        79.99  79.99   
61449     353770  IFX0026    1       74.90        74.90  74.95   
228147    486774  IFX0026    1       71.15        71.15  74.95   
119226    404835  IFX0121    1       64.99        64.99  64.99   
54250     347274  IFX0121    1       64.99        64.99  64.99   
58288     351014  IFX0076    1       54.90        54.90  59.95   
3097      302488  IFX0062    1       54.99        54.99  54.95   
106695    393646  IFX0062    1       54.99        54.99  54.95   
165747    431766  IFX0062    1       46.74        46.74  54.95   
146684    429053  IFX0062    1       54.99        54.99  54.95   
129746    414149  IFX0062    1       54.99        54.99  54.95   
212308    474876  IFX0062    1       52.24        52.24  54.95   
590       300123  IFX0024    1       49.99        49.99  49.99   
66258     358027  IFX0124    1       46.99        46.99  49.95   
108184    394994  IFX0124    1       44.64        44.64  49.95   
98256     386288  IFX0025    1       49.99        49.99  49.95   
69876     361270  IFX0123    1       46.99        46.99  49.95   
142639    425488  IFX0123    1       42.29        42.29  49.95   
172274    449290  IFX0025    1       28.04        28.04  49.95   
2228      301744  IFX0025    1       49.99        49.99  49.95   
29223     325649  IFX0123    1       46.99        46.99  49.95   
60966     353447  IFX0053    1       45.99        45.99  45.99   
57945     350665  IFX0053    1       45.99        45.99  45.99   
70011     361390  IFX0044    1       45.99        45.99  45.99   
53161     346394  IFX0044    1       45.99        45.99  45.99   
37381     332765  IFX0053    1       39.99        39.99  45.99   
67608     359321  IFX0044    1       45.99        45.99  45.99   
325       299865  IFX0044    1       43.69        43.69  45.99   
136777    420288  IFX0053    1       45.99        45.99  45.99   
81786     371774  IFX0053    1       45.99        45.99  45.99   
91277     380085  IFX0044    1       45.99        45.99  45.99   
99917     387720  IFX0053    1       45.99        45.99  45.99   
100108    387876  IFX0044    1       45.99        45.99  45.99   
20401     317685  IFX0044    1       43.69        43.69  45.99   
137526    420943  IFX0053    1       45.99        45.99  45.99   
137666    421052  IFX0053    1       45.99        45.99  45.99   
137796    421163  IFX0053    1       45.99        45.99  45.99   
169784    447319  IFX0044    1       39.09        39.09  45.99   
232278    489415  IFX0044    1       45.99        45.99  45.99   
267078    511087  IFX0053    1       45.99        45.99  45.99   
271679    514536  IFX0053    1       45.99        45.99  45.99   
20520     318132  IFX0053    1       43.69        43.69  45.99   
288684    526030  IFX0053    1       45.99        45.99  45.99   
8385      307443  IFX0044    1       45.99        45.99  45.99   
13737     312187  IFX0044    1       45.99        45.99  45.99   
164490    443520  IFX0132    1       22.94        22.94  44.95   
202586    466051  IFX0151    1       37.18        37.18  44.95   
24364     321484  IFX0151    1       44.99        44.99  44.95   
248332    499669  IFX0132    1       26.99        26.99  44.95   
273764    516220  IFX0151    1       42.74        42.74  44.95   
119840    405373  IFX0151    1       44.99        44.99  44.95   
164831    443202  IFX0131    1       38.24        38.24  44.95   
80388     370602  IFX0151    1       44.99      

In [899]:
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.name.str.contains('[Tt]oolkit|adhesive strips|Screwdriver|[Ss]uction [Cc]ups'))
                    &(~orders_comp.name.str.contains('[Bb]attery'))
                  , 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.name.str.contains('[Tt]oolkit|adhesive strips|Screwdriver|[Ss]uction [Cc]ups'))
                    &(~orders_comp.name.str.contains('[Bb]attery'))
                  , 'subcategory']
) = 'tools_apple_repair'

(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                    &(orders_comp.name.str.contains('[Bb]attery'))
                  , 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                    &(orders_comp.name.str.contains('[Bb]attery'))
                  , 'subcategory']
) = 'apple_battery'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  , 'category']
) = 'spare_parts'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  , 'subcategory']
) = 'apple_battery'


(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.name.str.contains('[Kk]it of [Tt]ools|[Rr]eplacement'))
                    &(~orders_comp.name.str.contains('[Bb]attery'))
                  , 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.desc.str.contains('[Kk]it of [Tt]ools|[Rr]eplacement'))
                    &(~orders_comp.desc.str.contains('[Bb]attery'))
                  , 'subcategory']
) = 'tools_apple_repair'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.name.str.contains('[Cc]able'))
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.name.str.contains('[Cc]able'))
                  , 'subcategory']
) = 'adapters_cables'

(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.category =='other')
                  , 'category']
) = 'tools'
(
    orders_comp.loc[(orders_comp.brand == 'iFixit')
                   &(orders_comp.category =='other')
                  , 'subcategory']
) = 'tools_apple_repair'

In [906]:
(
    orders_comp.loc[(orders_comp.brand == 'Seagate')
                     &(orders_comp.category =='other')
                    &(orders_comp.price<112)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False).head(500)
)

order_id        sku  qty  unit_price  total_price  price  \
20348     317975  SEA0046-A    1       78.65        78.65 111.99   
95146     383534    SEA0108    1       81.99        81.99 109.99   
103408    390764  SEA0102-A    4       79.65       318.60 109.99   
203144    466557    SEA0108    1       81.58        81.58 109.99   
241855    495725    SEA0108    1       81.58        81.58 109.99   
79113     369490    SEA0108    2       81.99       163.98 109.99   
169739    447274    SEA0108    1       76.34        76.34 109.99   
58392     351102    SEA0072    1       99.99        99.99 109.99   
45856     340081    SEA0072    1      109.99       109.99 109.99   
20885     318436    SEA0108    3       93.09       279.27 109.99   
142938    425752    SEA0108    2       77.83       155.66 109.99   
20221     317856    SEA0108    1       93.09        93.09 109.99   
218947    480899    SEA0108    1       81.58        81.58 109.99   
141748    424660    SEA0108    2       77.83       155.66 109.99   
19973     317644    SEA0074    1       92.99        92.99 109.99   
14313     312648    SEA0074    1       92.99        92.99 109.99   
189090    457533    SEA0072    1       99.79        99.79 109.99   
211048    473674    SEA0108    2       79.33       158.66 109.99   
171819    448919    SEA0108    2       76.34       152.68 109.99   
114908    401002    SEA0072    1      106.79       106.79 109.99   
105500    392609    SEA0108    1       88.58        88.58 109.99   
68084     359740    SEA0088    1       95.99        95.99 109.00   
115860    401817    SEA0088    1      107.79       107.79 109.00   
66188     357968    SEA0088    1       95.99        95.99 109.00   
89379     378384    SEA0088    1      107.80       107.80 109.00   
82995     372817    SEA0092    1       89.00        89.00 104.99   
122041    407310    SEA0092    1       87.59        87.59 104.99   
286911    524960    SEA0092    1       92.99        92.99 104.99   
80033     370308    SEA0092    1       77.99        77.99 104.99   
27447     324204    SEA0092    1       83.59        83.59 104.99   
68514     360108    SEA0092    1       85.99        85.99 104.99   
86443     375754    SEA0092    1       89.00        89.00 104.99   
60998     353477    SEA0092    1       85.99        85.99 104.99   
64569     356552    SEA0092    1       85.99        85.99 104.99   
67599     359315    SEA0100    1       86.99        86.99  99.99   
171542    448706    SEA0100    1       74.47        74.47  99.99   
64583     356562    SEA0100    1       86.99        86.99  99.99   
62213     354504    SEA0100    1       86.99        86.99  99.99   
216656    478819    SEA0100    1       77.39        77.39  99.99   
80123     370378    SEA0100    1       79.99        79.99  99.99   
145891    428253    SEA0100    1       79.58        79.58  99.99   
144557    427114    SEA0100    1       79.58        79.58  99.99   
96378     384647    SEA0100    2       79.99       159.98  99.99   
99062     387009    SEA0100    1       86.58        86.58  99.99   
237587    492960    SEA0100    1       79.58        79.58  99.99   
236082    491700    SEA0100    1       79.58        79.58  99.99   
139920    422871    SEA0100    1       79.58        79.58  99.99   
138025    421379    SEA0100    1       79.58        79.58  99.99   
234766    491100    SEA0100    1       79.58        79.58  99.99   
133485    417457    SEA0100    3       79.58       238.74  99.99   
132010    416163    SEA0100    1       79.58        79.58  99.99   
60399     352941    SEA0100    3       86.99       260.97  99.99   
126150    410959    SEA0100    1       79.58        79.58  99.99   
24365     321485    SEA0100    1       86.99        86.99  99.99   
217272    479353    SEA0100    3       79.58       238.74  99.99   
30479     326756    SEA0100    1       86.99        86.99  99.99   
199803    461721    SEA0100    1       79.58        79.58  99.99   
21807     319260    SEA0100    1       86.99        86.99  99.99

In [902]:
(
    orders_comp.loc[(orders_comp.brand == 'SanDisk')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'SanDisk')
                  , 'subcategory']
) = 'memory_apple_devices'

In [907]:
(
    orders_comp.loc[(orders_comp.brand == 'Seagate')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Seagate')
                    &(orders_comp.desc.str.contains('NAS'))
                  , 'subcategory']
) = 'servers'
(
    orders_comp.loc[(orders_comp.brand == 'Seagate')
                    &(~orders_comp.desc.str.contains('NAS'))
                  , 'subcategory']
) = 'computer_parts_memory'

In [908]:
orders_comp.brand.value_counts()

Apple                  13827
OWC                     3607
Pack                    2550
Belkin                  2256
LaCie                   2091
Crucial                 2027
Satechi                 1891
Western Digital         1859
Wacom                   1812
NewerTech               1575
iFixit                  1516
SanDisk                 1126
Seagate                  872
Griffin                  841
Samsung                  797
LG                       770
ZaggKeys                 743
Tucano                   703
Otterbox                 657
Dell                     642
JBL                      587
Synology                 558
Lifeproof                539
Philips                  533
Matias                   529
Moshi                    495
FCM                      473
Startech                 468
Spek SeeThru             444
Logitech                 435
Bose                     414
Kingston                 397
Mophie                   397
Trascend                 395
Macally       

In [944]:
(
    orders_comp.loc[(orders_comp.brand == 'FCM')
                     &(orders_comp.category =='other')
                #    &(orders_comp.price<112)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False)
)

order_id        sku  qty  unit_price  total_price  price  \
60302     352851  FCM0008-4    1      456.99       456.99 888.00   
70202     361583  FCM0008-4    1      456.99       456.99 888.00   
12330     311003  FCM0008-4    1      450.99       450.99 888.00   
28897     325372  FCM0008-4    1      498.99       498.99 888.00   
56513     349320  FCM0008-4    1      456.99       456.99 888.00   
15845     313935  FCM0038-4    1      278.99       278.99 607.92   
31306     327471  FCM0038-4    1      294.99       294.99 607.92   
77113     367762  FCM0008-2    1      228.99       228.99 444.00   
70932     362229  FCM0008-2    1      188.42       188.42 444.00   
82746     372592  FCM0008-2    1      228.99       228.99 444.00   
9496      308463  FCM0008-2    1      224.99       224.99 444.00   
86435     375746  FCM0008-2    1      228.99       228.99 444.00   
54891     347817  FCM0008-2    1      227.99       227.99 444.00   
30276     326577  FCM0008-2    1      224.09       224.09 444.00   
90372     379286  FCM0008-2    1      228.99       228.99 444.00   
103887    391186  FCM0008-2    1      189.25       189.25 444.00   
106464    393452  FCM0008-2    1      228.99       228.99 444.00   
11533     310288  FCM0017-4    1      210.99       210.99 279.96   
56392     349208  FCM0007-4    1      258.99       258.99 275.96   
27252     324041  FCM0007-4    1      266.99       266.99 275.96   
22956     320231  FCM0007-4    1      258.99       258.99 275.96   
327       299868  FCM0007-4    1      227.04       227.04 275.96   
87843     376962    FCM0045    1      216.99       216.99 244.99   
30817     327060    FCM0045    1      220.49       220.49 244.99   
271902    514708    FCM0045    1      181.99       181.99 244.99   
147773    430284    FCM0045    1      181.99       181.99 244.99   
237122    490703    FCM0045    1      135.36       135.36 244.99   
211230    473846    FCM0045    1      178.35       178.35 244.99   
58205     350924  FCM0038-2    1      148.99       148.99 151.98   
121968    407244  FCM0038-2    1      141.54       141.54 151.98   
4393      303763  FCM0038-2    1      138.99       138.99 151.98   
195810    461218  FCM0038-2    1      148.99       148.99 151.98   
58453     351176  FCM0038-2    1      148.99       148.99 151.98   
71911     363120  FCM0020-2    1      132.99       132.99 139.98   
106425    393423  FCM0020-2    1      132.99       132.99 139.98   
57543     350277  FCM0020-2    1      146.99       146.99 139.98   
52800     346077  FCM0020-2    1      146.99       146.99 139.98   
9134      308120  FCM0020-2    1      118.99       118.99 139.98   
11457     310213  FCM0020-2    1      128.99       128.99 139.98   
99312     387226  FCM0020-2    1      132.99       132.99 139.98   
24903     321913  FCM0020-2    1      135.99       135.99 139.98   
16602     314592  FCM0020-2    1      116.09       116.09 139.98   
13186     311175  FCM0020-2    1      128.99       128.99 139.98   
21165     318676  FCM0020-2    1      135.99       135.99 139.98   
67610     359323  FCM0020-2    1      132.99       132.99 139.98   
15170     313402  FCM0020-2    1      128.99       128.99 139.98   
8247      306371  FCM0020-2    1      128.99       128.99 139.98   
58920     351612  FCM0017-2    1      110.99       110.99 139.98   
167814    445692  FCM0017-2    1       90.94        90.94 139.98   
6950      306137  FCM0020-2    1      118.99       118.99 139.98   
132513    416067  FCM0017-2    1      125.09       125.09 139.98   
1287      300779  FCM0007-2    1      118.99       118.99 137.98   
4096      303472  FCM0007-2    1      118.99       118.99 137.98   
72257     362687  FCM0007-2    1      134.99       134.99 137.98   
54928     347851  FCM0007-2    1      128.99       128.99 137.98   
85302     374821  FCM0007-2    1      134.99       134.99 137.98   
76907     367598  FCM0007-2    1      134.99       134.99 137.98   
23409     320622  FCM0007-2    1      128.99       128.99 137.98

In [945]:
(
    orders_comp.loc[(orders_comp.brand == 'Griffin|Matias|FCM')
                    &(orders_comp.subcategory == 'other')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Griffin')
                    &(orders_comp.desc.str.contains('[Dd]ock|[Cc]harg|[Aa]dapter|[Cc]able'))
                  ,'subcategory']
) = 'adapters_cables'
(
    orders_comp.loc[(orders_comp.brand == 'FCM')
                  ,'subcategory']
) = 'computer_parts_memory'
(
    orders_comp.loc[(orders_comp.brand == 'Matias')
                    &(orders_comp.desc.str.contains('[Dd]ock|[Cc]harg|[Aa]dapter|[Cc]able'))
                  ,'subcategory']
) = 'keyboards'
(
    orders_comp.loc[(orders_comp.brand == 'Griffin')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  ,'subcategory']
) = 'external_battery'

(
    orders_comp.loc[(orders_comp.brand == 'Griffin')
                    &(orders_comp.desc.str.contains('[sS]upport'))
                  ,'subcategory']
) = 'support_apple_devices'
(
    orders_comp.loc[(orders_comp.brand == 'Griffin')
                    &(orders_comp.subcategory == 'other')
                  ,'subcategory']
) = 'cases_apple_devices'

In [938]:
(
    orders_comp.loc[(orders_comp.brand == 'Philips')
                     &(orders_comp.category =='other')
                #    &(orders_comp.price<112)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False)
)

order_id        sku  qty  unit_price  total_price  price  \
255262    503585    PHI0084    1      164.99       164.99 199.99   
252098    501598    PHI0084    1      164.99       164.99 199.99   
253340    502415    PHI0084    1      164.99       164.99 199.99   
219589    481482    PHI0084    1      146.27       146.27 199.99   
256975    504033    PHI0084    1      168.99       168.99 199.99   
249359    500221    PHI0084    1      164.99       164.99 199.99   
210386    473071    PHI0084    1      164.99       164.99 199.99   
267035    511048    PHI0084    1      168.99       168.99 199.99   
179089    452412    PHI0084    1      179.99       179.99 199.99   
216531    478718    PHI0084    1      164.99       164.99 199.99   
208834    471734    PHI0084    1      164.99       164.99 199.99   
204105    467361    PHI0078    1      164.98       164.98 199.95   
78249     368754    PHI0066    1      179.99       179.99 199.95   
5751      305056    PHI0066    1      179.99       179.99 199.95   
13727     312181    PHI0078    1      189.99       189.99 199.95   
201656    465231    PHI0066    1      179.99       179.99 199.95   
29425     325817    PHI0066    1      159.96       159.96 199.95   
201428    465043    PHI0078    1      164.98       164.98 199.95   
264749    509293    PHI0066    1      179.99       179.99 199.95   
171396    448566    PHI0078    1      170.99       170.99 199.95   
275956    517806  PHI0072-A    1      152.60       152.60 199.95   
18738     316478  PHI0072-A    1      131.95       131.95 199.95   
216944    479059    PHI0083    1      120.00       120.00 149.95   
210540    473205    PHI0083    1      120.00       120.00 149.95   
244640    497260    PHI0083    1      120.00       120.00 149.95   
234557    490988    PHI0075    1      106.99       106.99 139.95   
71027     362320    PHI0075    1      129.99       129.99 139.95   
71471     362749    PHI0075    1      129.99       129.99 139.95   
29715     326072    PHI0075    1      129.99       129.99 139.95   
93881     382431    PHI0075    1      112.99       112.99 139.95   
28656     325173    PHI0075    1      111.96       111.96 139.95   
56466     349281    PHI0075    1      129.99       129.99 139.95   
267004    511018    PHI0075    1      109.99       109.99 139.95   
28999     325463    PHI0075    1      111.96       111.96 139.95   
25678     322651    PHI0075    1      129.99       129.99 139.95   
19095     316800    PHI0075    1      123.49       123.49 139.95   
106592    393555    PHI0075    1      114.99       114.99 139.95   
108062    394875    PHI0075    1      109.24       109.24 139.95   
81645     371650    PHI0075    1      117.99       117.99 139.95   
180095    453106    PHI0086    1       90.99        90.99  99.95   
202712    466165    PHI0086    1       89.99        89.99  99.95   
172887    449757    PHI0086    1       81.89        81.89  99.95   
172493    449460    PHI0086    1       81.89        81.89  99.95   
211348    473960    PHI0086    1       85.49        85.49  99.95   
215666    477945    PHI0086    1       85.49        85.49  99.95   
240934    494946    PHI0086    1       89.99        89.99  99.95   
218595    480585    PHI0086    1       89.99        89.99  99.95   
275586    517464    PHI0086    1       84.99        84.99  99.95   
237426    492832    PHI0086    1       89.99        89.99  99.95   
235658    491714    PHI0086    1       89.99        89.99  99.95   
281606    521921    PHI0086    1       89.99        89.99  99.95   
277545    519160    PHI0086    1       84.99        84.99  99.95   
218404    480381    PHI0086    1       89.99        89.99  99.95   
216762    478906    PHI0086    1       85.49        85.49  99.95   
109330    396035    PHI0072    1       69.99        69.99  79.95   
33130     329102    PHI0072    1       69.99        69.99  79.95   
103597    390924    PHI0072    1       69.99        69.99  79.95   
56120     348972    PHI0054    1       75.90        75.90  79.95

In [939]:
(
    orders_comp.loc[(orders_comp.brand == 'Philips')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Philips')
                  , 'subcategory']
) = 'lighting'

In [912]:
(
    orders_comp.loc[(orders_comp.brand == 'Samsung')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Samsung')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Mm]onitor'))
                  , 'subcategory']
) = 'monitors'
(
    orders_comp.loc[(orders_comp.brand == 'Samsung')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.subcategory == 'other')
                  , 'subcategory']
) = 'computer_parts_memory'

In [935]:
(
    orders_comp.loc[(orders_comp.brand == 'LG|Dell'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'LG|Dell'), 'subcategory']
) = 'monitors'

In [924]:
(
    orders_comp.loc[(orders_comp.brand == 'QNAP'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'QNAP'), 'subcategory']
) = 'servers'

In [916]:
(
    orders_comp.loc[(orders_comp.brand == 'ZaggKeys')
                  , 'category']
) ='accessories'
(
    orders_comp.loc[(orders_comp.brand == 'ZaggKeys')
                    &(orders_comp.desc.str.contains('[Hh]eadset'))
                  , 'subcategory']
) ='headphones'
(
    orders_comp.loc[(orders_comp.brand == 'ZaggKeys')
                    &(orders_comp.desc.str.contains('[Kk]eyboard'))
                  , 'subcategory']
) = 'keyboards'
(
    orders_comp.loc[(orders_comp.brand == 'ZaggKeys')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.subcategory == 'other')
                  , 'subcategory']
) = 'cases_apple_devices'

In [918]:
(
    orders_comp.loc[(orders_comp.brand == 'Synology')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Synology')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('NAS'))
                  , 'subcategory']
) = 'servers'
(
    orders_comp.loc[(orders_comp.brand == 'Synology')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Rr]outer'))
                  , 'subcategory']
) = 'wifi'
(
    orders_comp.loc[(orders_comp.brand == 'Synology')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('DDR3 memory'))
                  , 'subcategory']
) = 'computer_parts_memory'
(
    orders_comp.loc[(orders_comp.brand == 'Synology')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('Anchor rails'))
                  , 'subcategory']
) = 'computer_parts'

In [943]:
(
    orders_comp.loc[(orders_comp.brand == 'Lifeproof|Moshi'), 'category']) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Lifeproof|Moshi')
                #    &(orders_comp.price<112)
                   &(orders_comp.name.str.contains('[Cc]ase'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'cases'

In [932]:
(
    orders_comp.loc[(orders_comp.brand == 'Spek SeeThru|Otterbox'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Spek SeeThru|Otterbox'), 'subcategory']
) = 'cases'

In [930]:

(
    orders_comp.loc[(orders_comp.brand == 'Tucano'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Tucano'), 'subcategory']
) = 'cases'

In [925]:
orders_comp.loc[orders_comp.category =='other'].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 19775 entries, 7 to 289885
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     19775 non-null  int64         
 1   sku          19775 non-null  object        
 2   qty          19775 non-null  int64         
 3   unit_price   19775 non-null  float64       
 4   total_price  19775 non-null  float64       
 5   price        19775 non-null  float64       
 6   name         19775 non-null  object        
 7   order_date   19775 non-null  datetime64[ns]
 8   brand        19775 non-null  object        
 9   desc         19775 non-null  object        
 10  in_stock     19775 non-null  int64         
 11  price_diff   19775 non-null  float64       
 12  disc_perc    19775 non-null  float64       
 13  category     19775 non-null  object        
 14  subcategory  19775 non-null  object        
dtypes: datetime64[ns](1), float64(5), int64(3), object(6

In [928]:
orders_comp['order_date'].describe(datetime_is_numeric=True)

count                            61322
mean     2017-09-13 01:36:01.958089984
min                2017-01-01 01:51:47
25%      2017-06-14 13:23:46.249999872
50%         2017-10-29 14:17:31.500000
75%      2017-12-25 21:52:34.750000128
max                2018-03-14 12:03:52
Name: order_date, dtype: object

In [942]:
(
    orders_comp.loc[(orders_comp.brand == 'Moshi')
                     &(orders_comp.category =='other')
                #    &(orders_comp.price<112)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False)
)

order_id        sku  qty  unit_price  total_price  price  \
244581    497210    MOS0244    2       69.99       139.98  89.99   
211350    473962    MOS0244    1       69.59        69.59  89.99   
253434    502499    MOS0244    1       69.99        69.99  89.99   
224453    484446    MOS0244    1       69.99        69.99  89.99   
221883    482862    MOS0194    1       69.99        69.99  69.99   
5382      304723    MOS0180    1       34.99        34.99  55.00   
52434     344213    MOS0087    1       25.99        25.99  55.00   
215590    477882    MOS0178    1       33.24        33.24  55.00   
133519    417484    MOS0218    1       39.99        39.99  50.00   
51695     345156    MOS0149    1       36.99        36.99  50.00   
172205    449157    MOS0220    1       33.99        33.99  50.00   
8578      307623    MOS0150    1       29.99        29.99  50.00   
1762      301261    MOS0147    1       34.99        34.99  50.00   
9382      308354    MOS0218    1       34.99        34.99  50.00   
98188     386229    MOS0220    1       39.99        39.99  50.00   
204373    467623    MOS0218    1       39.99        39.99  50.00   
97156     385328    MOS0149    2       36.99        73.98  50.00   
97150     385328    MOS0219    1       39.99        39.99  50.00   
261202    507300    MOS0218    1       39.99        39.99  50.00   
69092     360609    MOS0147    1       36.99        36.99  50.00   
69331     360814    MOS0193    1       32.99        32.99  50.00   
12645     311273    MOS0218    1       34.99        34.99  50.00   
80311     370537    MOS0218    1       39.99        39.99  50.00   
253054    502176    MOS0243    1       42.99        42.99  50.00   
14097     312467    MOS0193    1       32.99        32.99  50.00   
84137     373822    MOS0219    1       39.99        39.99  50.00   
15131     313365    MOS0218    1       34.99        34.99  50.00   
237748    493101    MOS0242    2       42.99        85.98  50.00   
15464     313647    MOS0220    1       39.99        39.99  50.00   
15523     313694    MOS0218    1       34.99        34.99  50.00   
247870    499306    MOS0176    1       28.49        28.49  50.00   
79513     369845    MOS0168    1       28.99        28.99  50.00   
81199     371279    MOS0219    1       39.99        39.99  50.00   
8281      307338    MOS0147    1       34.99        34.99  50.00   
98189     386229    MOS0218    1       39.99        39.99  50.00   
8142      307207    MOS0219    1       39.99        39.99  50.00   
63653     355781    MOS0176    1       29.99        29.99  50.00   
276191    517995    MOS0242    1       38.69        38.69  50.00   
4171      303546    MOS0219    1       39.99        39.99  50.00   
29591     325963    MOS0149    1       34.99        34.99  50.00   
123808    408916    MOS0149    1       36.99        36.99  50.00   
29549     325924    MOS0193    1       32.99        32.99  50.00   
141215    423741    MOS0220    1       29.75        29.75  50.00   
5563      304875    MOS0193    1       32.99        32.99  50.00   
157361    438135    MOS0193    1       28.04        28.04  50.00   
25776     322751    MOS0219    1       39.99        39.99  50.00   
271262    514196    MOS0148    1       36.99        36.99  50.00   
271709    479127    MOS0193    1       32.99        32.99  50.00   
26740     323607    MOS0218    1       39.99        39.99  50.00   
161177    441149    MOS0218    1       33.99        33.99  50.00   
107039    393945    MOS0193    1       32.99        32.99  50.00   
27385     324157    MOS0219    1       39.99        39.99  50.00   
24453     321564    MOS0165    1       46.90        46.90  49.99   
169536    447075    MOS0165    1       42.49        42.49  49.99   
65777     357583    MOS0103    1       26.99        26.99  45.00   
212001    474589    MOS0191    1       26.18        26.18  45.00   
202175    465670    MOS0115    1       36.99        36.99  45.00   
71638     362895    MOS0103    1       26.99        26.99  45.00

In [937]:
(
    orders_comp.loc[(orders_comp.brand == 'JBL')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'JBL')
                #    &(orders_comp.price<112)
                   &(orders_comp.name.str.contains('[Ss]peaker'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'speakers'
(
    orders_comp.loc[(orders_comp.brand == 'JBL')
                &(orders_comp.subcategory == 'other')
                  ,'subcategory']
) = 'headphones'

In [947]:
path = r'C:\Users\muell\Desktop\WBS\Project 2\coding_challenges\clean_csv'

In [1066]:
orders_comp.to_csv(path + '\orders_final.csv', index=False)

In [1065]:
orders_comp.loc[orders_comp.subcategory == 'other'].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 6927 entries, 23 to 289601
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   order_id     6927 non-null   int64         
 1   sku          6927 non-null   object        
 2   qty          6927 non-null   int64         
 3   unit_price   6927 non-null   float64       
 4   total_price  6927 non-null   float64       
 5   price        6927 non-null   float64       
 6   name         6927 non-null   object        
 7   order_date   6927 non-null   datetime64[ns]
 8   brand        6927 non-null   object        
 9   desc         6927 non-null   object        
 10  in_stock     6927 non-null   int64         
 11  price_diff   6927 non-null   float64       
 12  disc_perc    6927 non-null   float64       
 13  category     6927 non-null   object        
 14  subcategory  6927 non-null   object        
dtypes: datetime64[ns](1), float64(5), int64(3), object(6

In [952]:
orders_comp.brand.value_counts()

Apple                  13827
OWC                     3607
Pack                    2550
Belkin                  2256
LaCie                   2091
Crucial                 2027
Satechi                 1891
Western Digital         1859
Wacom                   1812
NewerTech               1575
iFixit                  1516
SanDisk                 1126
Seagate                  872
Griffin                  841
Samsung                  797
LG                       770
ZaggKeys                 743
Tucano                   703
Otterbox                 657
Dell                     642
JBL                      587
Synology                 558
Lifeproof                539
Philips                  533
Matias                   529
Moshi                    495
FCM                      473
Startech                 468
Spek SeeThru             444
Logitech                 435
Bose                     414
Kingston                 397
Mophie                   397
Trascend                 395
Macally       

In [1063]:
(
    orders_comp.loc[(orders_comp.brand == 'Repair')
                     &(orders_comp.subcategory =='other')
                #    &(orders_comp.price<112)
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ].sort_values('price', ascending=False)
)

order_id      sku  qty  unit_price  total_price  price  \
228385    480784  REP0358    1      249.99       249.99 299.99   
128992    407450  REP0188    1      199.99       199.99 209.99   
271534    506891  REP0350    1      199.99       199.99 199.99   
130940    415245  REP0194    1      129.00       129.00 179.99   
97186     385352  REP0396    1      189.99       189.99 119.99   
278496    519867  REP0396    1      119.99       119.99 119.99   
177059    446921  REP0396    1      189.99       189.99 119.99   
170910    448191  REP0396    1      170.99       170.99 119.99   
96584     384829  REP0323    1      159.99       159.99 109.99   
272540    515253  REP0323    1      109.99       109.99 109.99   
51745     345205  REP0323    1      159.99       159.99 109.99   
45887     340110  REP0313    1      139.99       139.99  99.99   
66538     358329  REP0313    1      139.99       139.99  99.99   
49267     343072  REP0313    1      139.99       139.99  99.99   
78820     369237  REP0313    1      139.99       139.99  99.99   
185126    455593  REP0209    1       98.99        98.99  99.99   
180361    453334  REP0300    1      119.99       119.99  99.99   
113176    399456  REP0300    1      119.99       119.99  99.99   
112728    399064  REP0300    1      119.99       119.99  99.99   
272799    515445  REP0313    1       99.99        99.99  99.99   
79458     369793  REP0238    1       99.99        99.99  89.99   
83856     373595  REP0238    1       99.99        99.99  89.99   
76806     367513  REP0238    1       99.99        99.99  89.99   
144051    426689  REP0238    1       99.99        99.99  89.99   
98502     386519  REP0238    1       99.99        99.99  89.99   
248351    499688  REP0238    1       99.99        99.99  89.99   
81924     371892  REP0238    1       99.99        99.99  89.99   
58809     351510  REP0238    1       99.99        99.99  89.99   
60174     352739  REP0238    1       99.99        99.99  89.99   
210968    473589  REP0238    1       99.99        99.99  89.99   
203647    466987  REP0238    1       99.99        99.99  89.99   
276466    518231  REP0238    1       89.99        89.99  89.99   
200531    464252  REP0238    1       99.99        99.99  89.99   
12281     310959  REP0238    1      119.99       119.99  89.99   
13204     311721  REP0238    1      119.99       119.99  89.99   
24761     321827  REP0238    1      119.99       119.99  89.99   
135785    419478  REP0238    1       99.99        99.99  89.99   
53087     346333  REP0238    1       99.99        99.99  89.99   
53406     346619  REP0238    1       99.99        99.99  89.99   
271210    514156  REP0238    1       89.99        89.99  89.99   
104398    391642  REP0238    1       99.99        99.99  89.99   
254639    503297  REP0327    1       69.99        69.99  69.99   
219762    481658  REP0365    1       69.99        69.99  69.99   
105852    392925  REP0319    1       69.99        69.99  69.99   
116071    402009  REP0348    1       69.99        69.99  69.99   
136730    420253  REP0341    1       69.99        69.99  69.99   
54401     347403  REP0391    1       69.99        69.99  69.99   
168514    446237  REP0365    1       62.99        62.99  69.99   
152602    434054  REP0362    1       62.99        62.99  69.99   
267580    511304  REP0369    1       69.99        69.99  69.99   
121699    406991  REP0240    1       69.99        69.99  69.99   
221846    482830  REP0240    1       69.00        69.00  69.99   
217446    479506  REP0240    1       39.00        39.00  69.99   
89316     378330  REP0250    1       59.99        59.99  69.90   
139852    422962  REP0307    1       59.99        59.99  59.99   
132160    416287  REP0307    1       59.99        59.99  59.99   
172630    449529  REP0309    1       53.99        53.99  59.99   
226153    485561  REP0274    1       59.99        59.99  59.99   
87259     376469  REP0306    1       59.99        59.99  59.99   
71439     362722  REP0274    1       59.99      

In [1064]:
(
    orders_comp.loc[(orders_comp.brand == 'Repair')
                  ,'category']
) = 'service'
(
    orders_comp.loc[(orders_comp.brand == 'Repair')
                    ,'subcategory']
) = 'repair'

In [1062]:
(
    orders_comp.loc[(orders_comp.brand == 'Service')
                  ,'category']
) = 'service'
(
    orders_comp.loc[(orders_comp.brand == 'Service')
                    ,'subcategory']
) = 'installation_repair'

In [1061]:
(
    orders_comp.loc[(orders_comp.brand == 'Puro')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Puro')
                    ,'subcategory']
) = 'iphone_cases'

In [1054]:
(
    orders_comp.loc[(orders_comp.brand == 'Twelve South')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Twelve South')
                    ,'subcategory']
) = 'cases'

In [1052]:
(
    orders_comp.loc[(orders_comp.brand == 'Minibatt')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Minibatt')
                    ,'subcategory']
) = 'charging'

In [1050]:
(
    orders_comp.loc[(orders_comp.brand == 'Jawbone')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Jawbone')
                    ,'subcategory']
) = 'monitors'

In [1048]:
(
    orders_comp.loc[(orders_comp.brand == 'LMP')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'LMP')
                    ,'subcategory']
) = 'hubs'
(
    orders_comp.loc[(orders_comp.brand == 'LMP')
                    &(orders_comp.desc.str.contains('keypad'))
                    ,'subcategory']
) = 'keyboards'

In [1046]:
(
    orders_comp.loc[(orders_comp.brand == 'Hoco Nike')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Hoco Nike')
                    ,'subcategory']
) = 'applewatch_straps'
(
    orders_comp.loc[(orders_comp.brand == 'Hoco Nike')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                    ,'subcategory']
) = 'external_battery'
(
    orders_comp.loc[(orders_comp.brand == 'Hoco Nike')
                    &(orders_comp.desc.str.contains('charging'))
                    ,'subcategory']
) = 'adapters_cables'

In [1044]:
(
    orders_comp.loc[(orders_comp.brand == 'Beats')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Beats')
                    ,'subcategory']
) = 'headphones'

In [1042]:
(
    orders_comp.loc[(orders_comp.brand == 'STM')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'STM')
                    ,'subcategory']
) = 'cases'

In [1040]:
(
    orders_comp.loc[(orders_comp.brand == 'BenQ')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'BenQ')
                    ,'subcategory']
) = 'monitors'

In [1038]:
(
    orders_comp.loc[(orders_comp.brand == 'Adonit')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Adonit')
                    ,'subcategory']
) = 'pencils'

In [1035]:
(
    orders_comp.loc[(orders_comp.brand == 'Sonos')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Sonos')
                    ,'subcategory']
) = 'speakers'

In [1033]:
(
    orders_comp.loc[(orders_comp.brand == 'Elgato')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Elgato')
                    ,'subcategory']
) = 'gadgets'
(
    orders_comp.loc[(orders_comp.brand == 'Elgato')
                    &(orders_comp.desc.str.contains('[Hh]ub'))
                    ,'subcategory']
) = 'hubs'
(
    orders_comp.loc[(orders_comp.brand == 'Elgato')
                    &(orders_comp.desc.str.contains('[Dd]ock'))
                    ,'subcategory']
) = 'adapters_cables'

In [1031]:
(
    orders_comp.loc[(orders_comp.brand == 'iOttie')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'iOttie')
                    ,'subcategory']
) = 'iphone_support'
(
    orders_comp.loc[(orders_comp.brand == 'iOttie')
                    &(orders_comp.desc.str.contains('charger'))
                    ,'subcategory']
) = 'iphone_charger'

In [1029]:
(
    orders_comp.loc[(orders_comp.brand == 'Moxie')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Moxie')
                    ,'subcategory']
) = 'iphone_cases'

In [1027]:
(
    orders_comp.loc[(orders_comp.brand == 'Thule')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Thule')
                    ,'subcategory']
) = 'macbook_cases'

In [1025]:
(
    orders_comp.loc[(orders_comp.brand == 'Plantronics')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Plantronics')
                    ,'subcategory']
) = 'headphones'

In [1023]:
(
    orders_comp.loc[(orders_comp.brand == 'Replacement')
                  ,'category']
) = 'spare-parts'
(
    orders_comp.loc[(orders_comp.brand == 'Replacement')
                    &(orders_comp.name.str.contains('screen'))
                    ,'subcategory']
) = 'iphone_screen'
(
    orders_comp.loc[(orders_comp.brand == 'Replacement')
                    &(orders_comp.name.str.contains('[Bb]attery'))
                    ,'subcategory']
) = 'iphone_battery'
(
    orders_comp.loc[(orders_comp.brand == 'Replacement')
                    &(orders_comp.name.str.contains('[Cc]able'))
                    ,'subcategory']
) = 'macbook_cable'

In [1021]:
(
    orders_comp.loc[(orders_comp.brand == 'G-Technology')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'G-Technology')
                    ,'subcategory']
) = 'memory'

In [1017]:
(
    orders_comp.loc[(orders_comp.brand == 'X-Doria')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'X-Doria')
                    &(orders_comp.name.str.contains('strap', case=False))
                    ,'subcategory']
) = 'applewatch_straps'
(
    orders_comp.loc[(orders_comp.brand == 'X-Doria')
                    &(orders_comp.name.str.contains('housing', case=False))
                    ,'subcategory']
) = 'applewatch_cases'
(
    orders_comp.loc[(orders_comp.brand == 'X-Doria')
                    &(orders_comp.name.str.contains('ipad', case=False))
                    ,'subcategory']
) = 'ipad_cases'
(
    orders_comp.loc[(orders_comp.brand == 'X-Doria')
                    &(orders_comp.name.str.contains('iphone', case=False))
                    ,'subcategory']
) = 'iphone_cases'

In [1015]:
(
    orders_comp.loc[(orders_comp.brand == 'Muvit')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Muvit')
                    ,'subcategory']
) = 'iphone_cases'

In [1013]:
(
    orders_comp.loc[(orders_comp.brand == 'Wowewa')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Wowewa')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                    ,'subcategory']
) = 'external_battery'
(
    orders_comp.loc[(orders_comp.brand == 'Wowewa')
                    &(orders_comp.desc.str.contains('[Pp]rotector'))
                    ,'subcategory']
) = 'iphone_cases'

In [1011]:
(
    orders_comp.loc[(orders_comp.brand == 'Kanex')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Kanex')
                    ,'subcategory']
) = 'adapters_cables'

In [1009]:
(
    orders_comp.loc[(orders_comp.brand == 'Sphero')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Sphero')
                    ,'subcategory']
) = 'gadgets'

In [1005]:
(
    orders_comp.loc[(orders_comp.brand == 'Hyper Pearl')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Hyper Pearl')
                    ,'subcategory']
) = 'gadgets'
(
    orders_comp.loc[(orders_comp.brand == 'Hyper Pearl')
                    &(orders_comp.desc.str.contains('[Hh]ub'))
                    ,'subcategory']
) = 'hubs'
(
    orders_comp.loc[(orders_comp.brand == 'Hyper Pearl')
                    &(orders_comp.name.str.contains('[Bb]attery'))
                    ,'subcategory']
) = 'external_battery'

In [1003]:
(
    orders_comp.loc[(orders_comp.brand == 'Netatmo')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Netatmo')
                    ,'subcategory']
) = 'gadgets'

In [1001]:
(
    orders_comp.loc[(orders_comp.brand == 'TrackR')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'TrackR')
                    ,'subcategory']
) = 'gadgets'

In [999]:
(
    orders_comp.loc[(orders_comp.brand == 'Toshiba')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Toshiba')
                    ,'subcategory']
) = 'memory'

In [997]:
(
    orders_comp.loc[(orders_comp.brand == 'Allocacoc')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Allocacoc')
                    ,'subcategory']
) = 'adapters_cables'

In [995]:
(
    orders_comp.loc[(orders_comp.brand == 'D-Link')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'D-Link')
                    ,'subcategory']
) = 'wifi'
(
    orders_comp.loc[(orders_comp.brand == 'D-Link')
                    &(orders_comp.desc.str.contains('[Cc]amera'))
                    ,'subcategory']
) = 'cameras'

In [994]:
(
    orders_comp.loc[(orders_comp.brand == 'TP-Link')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'TP-Link')
                    ,'subcategory']
) = 'wifi'
(
    orders_comp.loc[(orders_comp.brand == 'TP-Link')
                    &(orders_comp.desc.str.contains('[Cc]able'))
                    ,'subcategory']
) = 'adapters_cables'

In [990]:
(
    orders_comp.loc[(orders_comp.brand == 'Lexar')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Lexar')
                    ,'subcategory']
) = 'memory'

In [986]:
(
    orders_comp.loc[(orders_comp.brand == 'Macally')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Macally')
                   &(orders_comp.desc.str.contains('[Cc]able|[Aa]dapter'))
                    ,'subcategory']
) = 'adapters_cables'
(
    orders_comp.loc[(orders_comp.brand == 'Macally')
                   &(orders_comp.desc.str.contains('[Hh]ub'))
                    ,'subcategory']
) = 'hub'
(
    orders_comp.loc[(orders_comp.brand == 'Macally')
                   &(orders_comp.desc.str.contains('[Ll]amp'))
                    ,'subcategory']
) = 'lampcharge'
(
    orders_comp.loc[(orders_comp.brand == 'Macally')
                   &(orders_comp.desc.str.contains('outer box'))
                    ,'subcategory']
) = 'cases'

In [982]:
(
    orders_comp.loc[(orders_comp.brand == 'Trascend')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Trascend')
                  ,'subcategory']
) = 'computer_parts_memory'
(
    orders_comp.loc[(orders_comp.brand == 'Trascend')
                    &(orders_comp.desc.str.contains('DVD'))
                  ,'subcategory']
) = 'dvd'

In [979]:
(
    orders_comp.loc[(orders_comp.brand == 'Mophie')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Mophie')
                    &(orders_comp.desc.str.contains('[Bb]attery'))
                  ,'subcategory']
) = 'external_battery'
(
    orders_comp.loc[(orders_comp.brand == 'Mophie')
                    &(orders_comp.name.str.contains('[Cc]ase'))
                  ,'subcategory']
) = 'cases'
(
    orders_comp.loc[(orders_comp.brand == 'Mophie')
                    &(orders_comp.desc.str.contains('charging dock'))
                  ,'subcategory']
) = 'charging_iphone'

In [978]:
(
    orders_comp.loc[(orders_comp.brand == 'Kingston')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Kingston')
                  ,'subcategory']
) = 'computer_parts_memory'

In [964]:
(
    orders_comp.loc[(orders_comp.brand == 'Bose')
                  ,'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Bose')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Hh]eadphone|[Hh]eadset|[Ee]arphone'))
                  ,'subcategory']
) = 'headphones'
(
    orders_comp.loc[(orders_comp.brand == 'Bose')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Ss]peaker'))
                  ,'subcategory']
) = 'speakers'
(
    orders_comp.loc[(orders_comp.brand == 'Bose')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('[Mm]icrophone'))
                  ,'subcategory']
) = 'microphones'
(
    orders_comp.loc[(orders_comp.brand == 'Bose')
                 #  &(orders_comp.name.str.contains('[Cc]able'))
                    &(orders_comp.desc.str.contains('music system'))
                  ,'subcategory']
) = 'music_systems'

In [961]:
(
    orders_comp.loc[(orders_comp.brand == 'Logitech'), 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Logitech')
                #    &(orders_comp.price<112)
                   &(orders_comp.name.str.contains('[Cc]over|Folio'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'cases'
(
    orders_comp.loc[(orders_comp.brand == 'Logitech')
                #    &(orders_comp.price<112)
                   &(orders_comp.desc.str.contains('[Kk]eyboard'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'keyboards'
(
    orders_comp.loc[(orders_comp.brand == 'Logitech')
                #    &(orders_comp.price<112)
                   &(orders_comp.desc.str.contains('[Mm]ouse'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'mouses'
(
    orders_comp.loc[(orders_comp.brand == 'Logitech')
                #    &(orders_comp.price<112)
                   &(orders_comp.desc.str.contains('[Ss]peaker'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'speakers'
(
    orders_comp.loc[(orders_comp.brand == 'Logitech')
                #    &(orders_comp.price<112)
                   &(orders_comp.desc.str.contains('[Rr]emote [Cc]ontrol'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  ,'subcategory']
) = 'gadgets'

In [954]:
(
    orders_comp.loc[(orders_comp.brand == 'Startech')
                  , 'category']
) = 'accessories'
(
    orders_comp.loc[(orders_comp.brand == 'Startech')
                   &(orders_comp.desc.str.contains('[Cc]able|[Aa]dapter'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  , 'subcategory']
) = 'adapters_cables'
(
    orders_comp.loc[(orders_comp.brand == 'Startech')
                   &(orders_comp.desc.str.contains('[Hh]ub'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  , 'subcategory']
) = 'hubs'
(
    orders_comp.loc[(orders_comp.brand == 'Startech')
                   &(orders_comp.desc.str.contains('SuperDrive'))
                  #  &(orders_comp.desc.str.contains('[Dd]ock'))
                  , 'subcategory']
) = 'cases'


In [972]:
orders_comp.loc[orders_comp.category == 'iphones', 'subcategory'] = 'cases_iphone'
orders_comp.loc[orders_comp.category == 'iphones', 'category'] = 'accessories'

In [973]:
orders_comp.loc[orders_comp.category == 'iphones']

Empty DataFrame
Columns: [order_id, sku, qty, unit_price, total_price, price, name, order_date, brand, desc, in_stock, price_diff, disc_perc, category, subcategory]
Index: []